In [187]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt
import xgboost as xgb
from xgboost import XGBClassifier, XGBRegressor
from xgboost import plot_importance
from catboost import CatBoostRegressor
from matplotlib import pyplot
import shap
import random
from pandas.api.types import CategoricalDtype
from sklearn.model_selection import train_test_split
from sklearn.base import BaseEstimator
from sklearn.base import ClassifierMixin
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GroupKFold
from pprint import pprint
from bayes_opt import BayesianOptimization
import warnings
warnings.filterwarnings("ignore")

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.
from time import time
from tqdm import tqdm_notebook as tqdm
from collections import Counter
from scipy import stats
import lightgbm as lgb
from sklearn.metrics import cohen_kappa_score, mean_squared_error
from sklearn.model_selection import KFold, StratifiedKFold
import gc
import json
pd.set_option('display.max_columns', 1000)

In [2]:
def qwk3(a1, a2, max_rat=3):
    assert(len(a1) == len(a2))
    a1 = np.asarray(a1, dtype=int)
    a2 = np.asarray(a2, dtype=int)

    hist1 = np.zeros((max_rat + 1, ))
    hist2 = np.zeros((max_rat + 1, ))

    o = 0
    for k in range(a1.shape[0]):
        i, j = a1[k], a2[k]
        hist1[i] += 1
        hist2[j] += 1
        o +=  (i - j) * (i - j)

    e = 0
    for i in range(max_rat + 1):
        for j in range(max_rat + 1):
            e += hist1[i] * hist2[j] * (i - j) * (i - j)

    e = e / a1.shape[0]

    return 1 - o / e

In [3]:
def read_data():
    print('Reading train.csv file....')
    train = pd.read_csv('./Data/train.csv')
    print('Training.csv file have {} rows and {} columns'.format(train.shape[0], train.shape[1]))

    print('Reading test.csv file....')
    test = pd.read_csv('./Data/test.csv')
    print('Test.csv file have {} rows and {} columns'.format(test.shape[0], test.shape[1]))

    print('Reading train_labels.csv file....')
    train_labels = pd.read_csv('./Data/train_labels.csv')
    print('Train_labels.csv file have {} rows and {} columns'.format(train_labels.shape[0], train_labels.shape[1]))

    return train, test, train_labels

In [4]:
def encode_title(train, test, train_labels):
    # encode title
    train['title_event_code'] = list(map(lambda x, y: str(x) + '_' + str(y), train['title'], train['event_code']))
    test['title_event_code'] = list(map(lambda x, y: str(x) + '_' + str(y), test['title'], test['event_code']))
    all_title_event_code = list(set(train["title_event_code"].unique()).union(test["title_event_code"].unique()))
    # make a list with all the unique 'titles' from the train and test set
    list_of_user_activities = list(set(train['title'].unique()).union(set(test['title'].unique())))
    # make a list with all the unique 'event_code' from the train and test set
    list_of_event_code = list(set(train['event_code'].unique()).union(set(test['event_code'].unique())))
    list_of_event_id = list(set(train['event_id'].unique()).union(set(test['event_id'].unique())))
    # make a list with all the unique worlds from the train and test set
    list_of_worlds = list(set(train['world'].unique()).union(set(test['world'].unique())))
    # create a dictionary numerating the titles
    activities_map = dict(zip(list_of_user_activities, np.arange(len(list_of_user_activities))))
    activities_labels = dict(zip(np.arange(len(list_of_user_activities)), list_of_user_activities))
    activities_world = dict(zip(list_of_worlds, np.arange(len(list_of_worlds))))
    assess_titles = list(set(train[train['type'] == 'Assessment']['title'].value_counts().index).union(set(test[test['type'] == 'Assessment']['title'].value_counts().index)))
    # replace the text titles with the number titles from the dict
    train['title'] = train['title'].map(activities_map)
    test['title'] = test['title'].map(activities_map)
    train['world'] = train['world'].map(activities_world)
    test['world'] = test['world'].map(activities_world)
    train_labels['title'] = train_labels['title'].map(activities_map)
    win_code = dict(zip(activities_map.values(), (4100*np.ones(len(activities_map))).astype('int')))
    # then, it set one element, the 'Bird Measurer (Assessment)' as 4110, 10 more than the rest
    win_code[activities_map['Bird Measurer (Assessment)']] = 4110
    # convert text into datetime
    train['timestamp'] = pd.to_datetime(train['timestamp'])
    test['timestamp'] = pd.to_datetime(test['timestamp'])
    
    
    return train, test, train_labels, win_code, list_of_user_activities, list_of_event_code, activities_labels, assess_titles, list_of_event_id, all_title_event_code

In [22]:
def get_train_and_test(train, test):
    
    compiled_train = []
    compiled_test = []
    assessment_sessions_by_instid = {}
    
    # Loop through each train installation id
    for ins_id, user_sample in tqdm(train.groupby('installation_id', sort = False), 
                                   total = train['installation_id'].nunique()):
        compiled_train += get_data(user_sample, test_set = False)  
        
    reduce_train = pd.DataFrame(compiled_train)
    del compiled_train
    
    # Loop through each test installation id
    for ins_id, user_sample in tqdm(test.groupby('installation_id', sort = False), 
                                   total = test['installation_id'].nunique()):
        test_data = get_data(user_sample, test_set = True)
        compiled_test.append(test_data)   
        
    reduce_test = pd.DataFrame(compiled_test)
    del compiled_test
    
    categoricals = ['session_title']
    
    return reduce_train, reduce_test, categoricals

In [6]:
def get_data(user_sample, test_set=False):
    '''
    The user_sample is a DataFrame from train or test where the only one 
    installation_id is filtered
    And the test_set parameter is related with the labels processing, that is only requered
    if test_set=False
    '''
    # Constants and parameters declaration
    last_activity = 0
    
    user_activities_count = {'Clip':0, 'Activity': 0, 'Assessment': 0, 'Game':0}
    
    # new features: time spent in each activity
    last_session_time_sec = 0
    accuracy_groups = {0:0, 1:0, 2:0, 3:0}
    all_assessments = []
    accumulated_accuracy_group = 0
    accumulated_accuracy = 0
    accumulated_correct_attempts = 0 
    accumulated_uncorrect_attempts = 0
    accumulated_actions = 0
    counter = 0
    time_first_activity = float(user_sample['timestamp'].values[0])
    durations = []
    durations_game = []
    durations_activity = []
    last_accuracy_title = {'acc_' + title: -1 for title in assess_titles}
    last_game_time_title = {'lgt_' + title: 0 for title in assess_titles}
    ac_game_time_title = {'agt_' + title: 0 for title in assess_titles}
    ac_true_attempts_title = {'ata_' + title: 0 for title in assess_titles}
    ac_false_attempts_title = {'afa_' + title: 0 for title in assess_titles}
    event_code_count: Dict[str, int] = {ev: 0 for ev in list_of_event_code}
    event_id_count: Dict[str, int] = {eve: 0 for eve in list_of_event_id}
    title_count: Dict[str, int] = {eve: 0 for eve in activities_labels.values()} 
    title_event_code_count: Dict[str, int] = {t_eve: 0 for t_eve in all_title_event_code}
    session_count = 0
    
    # itarates through each session of one instalation_id
    for i, session in user_sample.groupby('game_session', sort=False):
        # i = game_session_id
        # session is a DataFrame that contain only one game_session
        
        # get some sessions information
        session_type = session['type'].iloc[0]
        session_title = session['title'].iloc[0]
        session_title_text = activities_labels[session_title]
        game_session = session['game_session'].iloc[0]          
            
        # for each assessment, and only this kind off session, the features below are processed
        # and a register are generated
        if (session_type == 'Assessment') & (test_set or len(session)>1):
            # search for event_code 4100, that represents the assessments trial
            all_attempts = session.query(f'event_code == {win_code[session_title]}')
            # then, check the numbers of wins and the number of losses
            true_attempts = all_attempts['event_data'].str.contains('true').sum()
            false_attempts = all_attempts['event_data'].str.contains('false').sum()
            # copy a dict to use as feature template, it's initialized with some itens: 
            # {'Clip':0, 'Activity': 0, 'Assessment': 0, 'Game':0}
            features = user_activities_count.copy()
            features.update(last_accuracy_title.copy())
            features.update(event_code_count.copy())
            features.update(title_count.copy())
            features.update(event_id_count.copy())
            features.update(title_event_code_count.copy())
            features.update(last_game_time_title.copy())
            features.update(ac_game_time_title.copy())
            features.update(ac_true_attempts_title.copy())
            features.update(ac_false_attempts_title.copy())
            features['installation_session_count'] = session_count
            
            variety_features = [('var_event_code', event_code_count), 
                                ('var_event_id', event_id_count), 
                                ('var_title', title_count), 
                                ('var_title_event_code', title_event_code_count)]
            
            for name, dict_counts in variety_features:
                arr = np.array(list(dict_counts.values()))
                features[name] = np.count_nonzero(arr)
                
            # get installation_id for aggregated features
            features['installation_id'] = session['installation_id'].iloc[-1]
            features['game_session'] = game_session
            # add title as feature, remembering that title represents the name of the game
            features['session_title'] = session['title'].iloc[0]
            # the 4 lines below add the feature of the history of the trials of this player
            # this is based on the all time attempts so far, at the moment of this assessment
            features['accumulated_correct_attempts'] = accumulated_correct_attempts
            features['accumulated_uncorrect_attempts'] = accumulated_uncorrect_attempts
            accumulated_correct_attempts += true_attempts 
            accumulated_uncorrect_attempts += false_attempts
            
            # ----------------------------------------------
            ac_true_attempts_title['ata_' + session_title_text] += true_attempts
            ac_false_attempts_title['afa_' + session_title_text] += false_attempts
            
            
            last_game_time_title['lgt_' + session_title_text] = session['game_time'].iloc[-1]
            ac_game_time_title['agt_' + session_title_text] += session['game_time'].iloc[-1]
            # ----------------------------------------------
            
            # the time spent in the app so far
            if durations == []:
                features['duration_mean'] = 0
                features['duration_std'] = 0
                features['last_duration'] = 0
                features['duration_max'] = 0
            else:
                features['duration_mean'] = np.mean(durations)
                features['duration_std'] = np.std(durations)
                features['last_duration'] = durations[-1]
                features['duration_max'] = np.max(durations)
            durations.append((session.iloc[-1, 2] - session.iloc[0, 2] ).seconds)
            
            if durations_game == []:
                features['duration_game_mean'] = 0
                features['duration_game_std'] = 0
                features['game_last_duration'] = 0
                features['game_max_duration'] = 0
            else:
                features['duration_game_mean'] = np.mean(durations_game)
                features['duration_game_std'] = np.std(durations_game)
                features['game_last_duration'] = durations_game[-1]
                features['game_max_duration'] = np.max(durations_game)
                
            if durations_activity == []:
                features['duration_activity_mean'] = 0
                features['duration_activity_std'] = 0
                features['game_activity_duration'] = 0
                features['game_activity_max'] = 0
            else:
                features['duration_activity_mean'] = np.mean(durations_activity)
                features['duration_activity_std'] = np.std(durations_activity)
                features['game_activity_duration'] = durations_activity[-1]
                features['game_activity_max'] = np.max(durations_activity)
            
            # the accuracy is the all time wins divided by the all time attempts
            features['accumulated_accuracy'] = accumulated_accuracy/counter if counter > 0 else 0
            accuracy = true_attempts/(true_attempts+false_attempts) if (true_attempts+false_attempts) != 0 else 0
            accumulated_accuracy += accuracy
            last_accuracy_title['acc_' + session_title_text] = accuracy
            # a feature of the current accuracy categorized
            # it is a counter of how many times this player was in each accuracy group
            if accuracy == 0:
                features['accuracy_group'] = 0
            elif accuracy == 1:
                features['accuracy_group'] = 3
            elif accuracy == 0.5:
                features['accuracy_group'] = 2
            else:
                features['accuracy_group'] = 1
            features.update(accuracy_groups)
            accuracy_groups[features['accuracy_group']] += 1
            # mean of the all accuracy groups of this player
            features['accumulated_accuracy_group'] = accumulated_accuracy_group/counter if counter > 0 else 0
            accumulated_accuracy_group += features['accuracy_group']
            # how many actions the player has done so far, it is initialized as 0 and updated some lines below
            features['accumulated_actions'] = accumulated_actions
            
            # there are some conditions to allow this features to be inserted in the datasets
            # if it's a test set, all sessions belong to the final dataset
            # it it's a train, needs to be passed throught this clausule: session.query(f'event_code == {win_code[session_title]}')
            # that means, must exist an event_code 4100 or 4110
            if test_set:
                all_assessments.append(features)
            elif true_attempts+false_attempts > 0:
                all_assessments.append(features)
                
            counter += 1
            
        if session_type == 'Game':
            durations_game.append((session.iloc[-1, 2] - session.iloc[0, 2] ).seconds)
            
        if session_type == 'Activity':
            durations_activity.append((session.iloc[-1, 2] - session.iloc[0, 2] ).seconds)
                
        
        session_count += 1
        # this piece counts how many actions was made in each event_code so far
        def update_counters(counter: dict, col: str):
                num_of_session_count = Counter(session[col])
                for k in num_of_session_count.keys():
                    x = k
                    if col == 'title':
                        x = activities_labels[k]
                    counter[x] += num_of_session_count[k]
                return counter
            
        event_code_count = update_counters(event_code_count, "event_code")
        event_id_count = update_counters(event_id_count, "event_id")
        title_count = update_counters(title_count, 'title')
        title_event_code_count = update_counters(title_event_code_count, 'title_event_code')

        # counts how many actions the player has done so far, used in the feature of the same name
        accumulated_actions += len(session)
        if last_activity != session_type:
            user_activities_count[session_type] += 1
            last_activitiy = session_type 
                        
    # if it't the test_set, only the last assessment must be predicted, the previous are scraped
    if test_set:
        return all_assessments[-1]
    # in the train_set, all assessments goes to the dataset
    return all_assessments

In [13]:
def remove_dead_weight(df, train_labels, test_set=False):
    #df = df[df['world'] != 'NONE']

    # filtering by ids that took assessments
    ids_w_assessments = df[df['type'] == 'Assessment']['installation_id'].drop_duplicates()
    df = df[df['installation_id'].isin(ids_w_assessments)]
    
    #If training set then make sure the installation ids are in the labels and remove assements not in the labels
    if test_set == False:
        # drop data whose installation does not contain any scored assessments in train_labels
        df = df[df['installation_id'].isin(train_labels['installation_id'].unique())]

        assessments = df[df.type == 'Assessment']
        assessments = assessments[~assessments.game_session.isin(train_labels.game_session)]
        df = df[~df.game_session.isin(assessments.game_session)]
        df.reset_index(drop=True, inplace=True)
        
    return df

In [113]:
# Min Max
def create_min_max(train, test, categoricals):
    tmp_train = train.copy()
    tmp_test = test.copy()
    tmp_train = tmp_train.apply(lambda x: (x - x.min()) / (x.max() - x.min())).fillna(0)
    tmp_test = tmp_test.apply(lambda x: (x - x.min()) / (x.max() - x.min())).fillna(0)
    
    return tmp_train, tmp_test

In [9]:
# Create Catagoricals
def create_cats(train, test, categoricals):
    tmp_train = train.copy()
    tmp_test = test.copy()
    tmp_train['session_title'] = tmp_train['session_title'].astype(CategoricalDtype(categories=activities_labels))
    tmp_test['session_title'] = tmp_test['session_title'].astype(CategoricalDtype(categories=activities_labels))
    #tmp_train['world'] = tmp_train['world'].astype(CategoricalDtype(categories=[0, 1, 2]))
    #tmp_test['world'] = tmp_test['world'].astype(CategoricalDtype(categories=[0, 1, 2]))
    tmp_train = pd.get_dummies(tmp_train, prefix=categoricals)
    tmp_test = pd.get_dummies(tmp_test, prefix=categoricals)
    
    return tmp_train, tmp_test

In [10]:
def stract_hists(feature, train, test, adjust=False, plot=False):
    n_bins = 10
    train_data = train[feature]
    test_data = test[feature]
    if adjust:
        test_data *= train_data.mean() / test_data.mean()
    perc_90 = np.percentile(train_data, 95)
    train_data = np.clip(train_data, 0, perc_90)
    test_data = np.clip(test_data, 0, perc_90)
    train_hist = np.histogram(train_data, bins=n_bins)[0] / len(train_data)
    test_hist = np.histogram(test_data, bins=n_bins)[0] / len(test_data)
    msre = mean_squared_error(train_hist, test_hist)
    if plot:
        print(msre)
        plt.bar(range(n_bins), train_hist, color='blue', alpha=0.5)
        plt.bar(range(n_bins), test_hist, color='red', alpha=0.5)
        plt.show()
    return msre

In [11]:
# get prediction
def get_class_pred(pred, train_t):
    """
    Fast cappa eval function for lgb.
    """
    dist = Counter(train_t['accuracy_group'])
    for k in dist:
        dist[k] /= len(train_t)
    
    acum = 0
    bound = {}
    for i in range(3):
        acum += dist[i]
        bound[i] = np.percentile(pred, acum * 100)

    def classify(x):
        if x <= bound[0]:
            return 0
        elif x <= bound[1]:
            return 1
        elif x <= bound[2]:
            return 2
        else:
            return 3

    y_pred = np.array(list(map(classify, pred)))
    
    return y_pred


In [130]:
def preprocess(reduce_train, reduce_test):
    for df in [reduce_train, reduce_test]:
        df['installation_session_count'] = df.groupby(['installation_id'])['Clip'].transform('count')
        df['installation_duration_mean'] = df.groupby(['installation_id'])['duration_mean'].transform('mean')
        #df['installation_duration_std'] = df.groupby(['installation_id'])['duration_mean'].transform('std')
        df['installation_title_nunique'] = df.groupby(['installation_id'])['session_title'].transform('nunique')
        
        df['sum_event_code_count'] = df[[2050, 4100, 4230, 5000, 4235, 2060, 4110, 5010, 2070, 2075, 2080, 2081, 2083, 3110, 4010, 3120, 3121, 4020, 4021, 
                                        4022, 4025, 4030, 4031, 3010, 4035, 4040, 3020, 3021, 4045, 2000, 4050, 2010, 2020, 4070, 2025, 2030, 4080, 2035, 
                                        2040, 4090, 4220, 4095]].sum(axis = 1)
        
        df['installation_event_code_count_mean'] = df.groupby(['installation_id'])['sum_event_code_count'].transform('mean')
        #df['installation_event_code_count_std'] = df.groupby(['installation_id'])['sum_event_code_count'].transform('std')
        
    features = reduce_train.loc[(reduce_train.sum(axis=1) != 0), (reduce_train.sum(axis=0) != 0)].columns # delete useless columns
    features = [x for x in features if x not in cols_to_drop]
    
    return reduce_train, reduce_test, features

In [131]:
# read data
train, test, train_labels = read_data()

Reading train.csv file....
Training.csv file have 11341042 rows and 11 columns
Reading test.csv file....
Test.csv file have 1156414 rows and 11 columns
Reading train_labels.csv file....
Train_labels.csv file have 17690 rows and 7 columns


In [132]:
# remove unwanted data
train = remove_dead_weight(train, train_labels, test_set=False)
test = remove_dead_weight(test, train_labels, test_set=True)

In [133]:
# get usefull dict with maping encode
train, test, train_labels, win_code, list_of_user_activities, list_of_event_code, activities_labels, assess_titles, list_of_event_id, all_title_event_code = encode_title(train, test, train_labels)

In [134]:
# tranform function to get the train and test set
reduce_train, reduce_test, categoricals = get_train_and_test(train, test)

This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


In [135]:
# Delete train and test to free up resources
del train, test
gc.collect()

In [136]:
# Add the accuracy group vals
reduce_train = reduce_train.set_index('game_session')
train_labels = train_labels.set_index('game_session')
reduce_train.update(train_labels)

In [137]:
# Reset index
reduce_train = reduce_train.reset_index()
reduce_test = reduce_test.reset_index()
train_labels = train_labels.reset_index()

In [138]:
# Create the cols to drop for training
cols_to_drop = ['accuracy_group', 'game_session', 'installation_id']

In [139]:
reduce_train, reduce_test, features = preprocess(reduce_train, reduce_test)

In [140]:
# Go through and find high correlations. Add to remove list if so
counter = 0
to_remove = []
for feat_a in features:
    for feat_b in features:
        if feat_a != feat_b and feat_a not in to_remove and feat_b not in to_remove:
            c = np.corrcoef(reduce_train[feat_a], reduce_train[feat_b])[0][1]
            if c > 0.995:
                counter += 1
                to_remove.append(feat_b)
                print('{}: FEAT_A: {} FEAT_B: {} - Correlation: {}'.format(counter, feat_a, feat_b, c))

1: FEAT_A: Clip FEAT_B: 27253bdc - Correlation: 0.9999999999999999
2: FEAT_A: 2050 FEAT_B: 2040 - Correlation: 0.9965259434878112
3: FEAT_A: 2050 FEAT_B: 26fd2d99 - Correlation: 0.9965084543995767
4: FEAT_A: 2050 FEAT_B: 2b9272f4 - Correlation: 0.999983903006877
5: FEAT_A: 2050 FEAT_B: dcaede90 - Correlation: 0.9965259434878112
6: FEAT_A: 2050 FEAT_B: 73757a5e - Correlation: 0.9998050146714003
7: FEAT_A: 2050 FEAT_B: 37c53127 - Correlation: 1.0
8: FEAT_A: 2050 FEAT_B: 08fd73f3 - Correlation: 0.9966123918733636
9: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_2030 - Correlation: 0.9966123918733636
10: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_2050 - Correlation: 1.0
11: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_3021 - Correlation: 0.9998050146714003
12: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_2040 - Correlation: 0.9965259434878112
13: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_3121 - Correlation: 0.999983903006877
14: FEAT_A: 2050 FEAT_B: Scrub-A-Dub_2020 - Correlation: 0.9965084543995767
15: FEAT_A: 3110 FEAT_B: 3010 - Correlation: 

110: FEAT_A: beb0a7b9 FEAT_B: b88f38da - Correlation: 0.9999125179829765
111: FEAT_A: beb0a7b9 FEAT_B: Fireworks (Activity)_3110 - Correlation: 0.9999125179829765
112: FEAT_A: beb0a7b9 FEAT_B: Fireworks (Activity)_3010 - Correlation: 0.9999999999999999
113: FEAT_A: 28f975ea FEAT_B: Air Show_4020 - Correlation: 1.0
114: FEAT_A: 6077cc36 FEAT_B: Bird Measurer (Assessment)_4080 - Correlation: 1.0
115: FEAT_A: ecc36b7f FEAT_B: Bubble Bath_4095 - Correlation: 1.0
116: FEAT_A: 7dfe6d8a FEAT_B: Leaf Leader_4070 - Correlation: 1.0
117: FEAT_A: b012cd7f FEAT_B: e5c9df6f - Correlation: 0.9990885395773591
118: FEAT_A: b012cd7f FEAT_B: 3afde5dd - Correlation: 0.9999689260314969
119: FEAT_A: b012cd7f FEAT_B: Leaf Leader_2030 - Correlation: 1.0
120: FEAT_A: b012cd7f FEAT_B: Leaf Leader_3121 - Correlation: 0.9990885395773591
121: FEAT_A: b012cd7f FEAT_B: Leaf Leader_3021 - Correlation: 0.9999689260314969
122: FEAT_A: 76babcde FEAT_B: Dino Dive_4070 - Correlation: 1.0
123: FEAT_A: 0330ab6a FEAT_B: 223

216: FEAT_A: e37a2b78 FEAT_B: Bird Measurer (Assessment)_4110 - Correlation: 0.9982548122198929
217: FEAT_A: e37a2b78 FEAT_B: Bird Measurer (Assessment)_3020 - Correlation: 0.9992191329664102
218: FEAT_A: e37a2b78 FEAT_B: Bird Measurer (Assessment)_3120 - Correlation: 1.0
219: FEAT_A: e37a2b78 FEAT_B: afa_Bird Measurer (Assessment) - Correlation: 0.9983241920747606
220: FEAT_A: df4940d3 FEAT_B: 67439901 - Correlation: 0.999935162643595
221: FEAT_A: df4940d3 FEAT_B: Bottle Filler (Activity)_3010 - Correlation: 0.999935162643595
222: FEAT_A: df4940d3 FEAT_B: Bottle Filler (Activity)_3110 - Correlation: 1.0
223: FEAT_A: 857f21c0 FEAT_B: Bubble Bath_4040 - Correlation: 1.0
224: FEAT_A: ec138c1c FEAT_B: Bird Measurer (Assessment)_2020 - Correlation: 1.0
225: FEAT_A: 89aace00 FEAT_B: e5734469 - Correlation: 0.9998406115110341
226: FEAT_A: 89aace00 FEAT_B: Dino Drink_3120 - Correlation: 1.0
227: FEAT_A: 89aace00 FEAT_B: Dino Drink_3020 - Correlation: 0.9998406115110341
228: FEAT_A: 51102b85 F

321: FEAT_A: 7d5c30a2 FEAT_B: Dino Dive_2060 - Correlation: 1.0
322: FEAT_A: 262136f4 FEAT_B: Leaf Leader_4020 - Correlation: 1.0
323: FEAT_A: 56817e2b FEAT_B: cb6010f8 - Correlation: 0.9990475739429793
324: FEAT_A: 56817e2b FEAT_B: 47026d5f - Correlation: 0.9993683693704353
325: FEAT_A: 56817e2b FEAT_B: Chow Time_3121 - Correlation: 0.9990475739429793
326: FEAT_A: 56817e2b FEAT_B: Chow Time_3021 - Correlation: 0.9993683693704353
327: FEAT_A: 56817e2b FEAT_B: Chow Time_2030 - Correlation: 0.9999999999999998
328: FEAT_A: 4a4c3d21 FEAT_B: Bird Measurer (Assessment)_4025 - Correlation: 1.0
329: FEAT_A: 5e812b27 FEAT_B: Sandcastle Builder (Activity)_4030 - Correlation: 1.0
330: FEAT_A: 832735e1 FEAT_B: ab3136ba - Correlation: 0.9998637945770231
331: FEAT_A: 832735e1 FEAT_B: Dino Dive_3110 - Correlation: 0.9998637945770231
332: FEAT_A: 832735e1 FEAT_B: Dino Dive_3010 - Correlation: 1.0
333: FEAT_A: 7525289a FEAT_B: 45d01abe - Correlation: 0.9982095234026296
334: FEAT_A: 7525289a FEAT_B: Bir

426: FEAT_A: 5348fd84 FEAT_B: Cauldron Filler (Assessment)_4040 - Correlation: 1.0
427: FEAT_A: 9ee1c98c FEAT_B: Sandcastle Builder (Activity)_4021 - Correlation: 0.9999999999999999
428: FEAT_A: 02a42007 FEAT_B: Fireworks (Activity)_4030 - Correlation: 1.0
429: FEAT_A: 6bf9e3e1 FEAT_B: Happy Camel_4040 - Correlation: 0.9999999999999999
430: FEAT_A: 74e5f8a7 FEAT_B: Dino Drink_4020 - Correlation: 1.0
431: FEAT_A: 0ce40006 FEAT_B: Happy Camel_4080 - Correlation: 1.0
432: FEAT_A: 155f62a4 FEAT_B: 5b49460a - Correlation: 1.0
433: FEAT_A: 155f62a4 FEAT_B: Chest Sorter (Assessment)_2000 - Correlation: 1.0
434: FEAT_A: 155f62a4 FEAT_B: Chest Sorter (Assessment)_2020 - Correlation: 1.0
435: FEAT_A: 37db1c2f FEAT_B: Happy Camel_4045 - Correlation: 1.0
436: FEAT_A: 05ad839b FEAT_B: Happy Camel_4090 - Correlation: 1.0
437: FEAT_A: de26c3a6 FEAT_B: Flower Waterer (Activity)_4020 - Correlation: 0.9999999999999999
438: FEAT_A: cfbd47c8 FEAT_B: Chow Time_4030 - Correlation: 1.0
439: FEAT_A: 87d743c1 

In [141]:
# Go through again a look for features to remove
to_exclude = [] 
ajusted_test = reduce_test.copy()
for feature in ajusted_test.columns:
    if feature not in cols_to_drop:
        try:
            data = reduce_train[feature]
            train_mean = data.mean()
            data = ajusted_test[feature] 
            test_mean = data.mean()
            error = stract_hists(feature, train=reduce_train, test=reduce_test, adjust=True)
            ajust_factor = train_mean / test_mean
            if ajust_factor > 10 or ajust_factor < 0.1:# or error > 0.01:
                to_exclude.append(feature)
                print(feature, train_mean, test_mean, error)
            else:
                ajusted_test[feature] *= ajust_factor
        except:
            to_exclude.append(feature)

acc_Cart Balancer (Assessment) -0.03721019762851306 -0.47065833333333335 0.008226900025148906


divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
invalid value encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars


6aeafed4 0.14703222159412097 0.008 0.0


divide by zero encountered in double_scalars


eb2c19cd 0.15596382136800452 0.008 0.0


...

Mushroom Sorter (Assessment)_4090 0.15596382136800452 0.008 0.0


divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars


Bubble Bath_4090 0.14703222159412097 0.008 0.0


invalid value encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars
divide by zero encountered in double_scalars


installation_session_count 14.58383267382702 1.0 0.1127006932086135


In [142]:
# Create final feature list removing the unwanted ones
features = [x for x in features if x not in (to_exclude + to_remove)]

In [143]:
# Drop uneeded
all_features = features
train = reduce_train[all_features].copy()
train['installation_id'] = reduce_train['installation_id']
test = ajusted_test[all_features].copy()

In [144]:
X_train, X_valid, y_train, y_valid = train_test_split(train.drop(['installation_id'], axis=1), reduce_train['accuracy_group'], test_size=0.3)
del train, reduce_test
gc.collect()

In [145]:
# Create Min Max
X_train_with_cats, X_valid_with_cats = create_cats(X_train, X_valid, categoricals)
X_train_with_cats, X_valid_with_cats = create_min_max(X_train_with_cats, X_valid_with_cats, categoricals)
X_train_with_cats.columns = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in X_train_with_cats.columns]
X_valid_with_cats.columns = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in X_valid_with_cats.columns]

In [233]:
# Random Forrest Classifier
from sklearn.ensemble import RandomForestClassifier
def RF_Bayesian(max_depth, max_features, min_samples_leaf, min_samples_split, n_estimators):
    
    params = {
        'bootstrap': False,
        'max_depth': int(max_depth),
        'max_features': int(max_features),
        'min_samples_leaf': int(min_samples_leaf),
        'min_samples_split': int(min_samples_split),
        'n_estimators': int(n_estimators),
        'n_jobs': -1
    }
    
    model = RandomForestClassifier(**params)
    model.fit(X_train_with_cats, y_train)
    pred = model.predict(X_valid_with_cats)
    
    return qwk3(y_valid, pred)

In [235]:
init_points = 25
n_iter = 50

bounds_RF = {
    'max_depth': (20, 60),
    'max_features': (15, 75),
    'min_samples_leaf': (2, 10),
    'min_samples_split': (2, 10),
    'n_estimators': (1000, 3000)
}

RF_BO = BayesianOptimization(RF_Bayesian, bounds_RF, random_state=1029)

with warnings.catch_warnings():
    warnings.filterwarnings('ignore')
    RF_BO.maximize(init_points=init_points, n_iter=n_iter, acq='ucb', xi=0.0, alpha=1e-6)

|   iter    |  target   | max_depth | max_fe... | min_sa... | min_sa... | n_esti... |
-------------------------------------------------------------------------------------
|  1        |  0.5434   |  21.64    |  39.59    |  6.71     |  9.199    |  1.242e+0 |
|  2        |  0.5507   |  26.81    |  71.41    |  6.762    |  4.685    |  1.883e+0 |
|  3        |  0.5214   |  39.83    |  20.27    |  4.193    |  7.28     |  1.161e+0 |
|  4        |  0.5523   |  21.55    |  55.51    |  3.499    |  9.515    |  2.742e+0 |
|  5        |  0.5442   |  34.33    |  49.07    |  9.034    |  5.62     |  2.41e+03 |
|  6        |  0.5522   |  51.85    |  71.63    |  4.431    |  9.276    |  2e+03    |
|  7        |  0.5374   |  21.55    |  31.03    |  2.931    |  4.272    |  1.981e+0 |
|  8        |  0.5505   |  50.29    |  57.41    |  6.224    |  8.961    |  1.046e+0 |
|  9        |  0.5326   |  32.33    |  25.1     |  5.408    |  8.215    |  2.069e+0 |
|  10       |  0.5439   |  31.66    |  43.28    |  7.3

|  58       |  0.5576   |  23.84    |  73.44    |  2.549    |  9.184    |  1.918e+0 |
|  59       |  0.558    |  23.92    |  73.95    |  2.569    |  9.231    |  1.035e+0 |
|  60       |  0.5568   |  21.72    |  71.45    |  2.22     |  9.885    |  1.211e+0 |
|  61       |  0.5575   |  20.39    |  74.58    |  2.06     |  6.082    |  2.796e+0 |
|  62       |  0.5567   |  50.18    |  73.7     |  2.884    |  9.29     |  2.855e+0 |
|  63       |  0.5516   |  24.75    |  74.78    |  2.192    |  2.803    |  2.512e+0 |
|  64       |  0.5454   |  58.55    |  74.76    |  9.641    |  6.6      |  1.342e+0 |
|  65       |  0.5416   |  22.74    |  56.58    |  9.754    |  9.649    |  1.922e+0 |
|  66       |  0.5539   |  53.29    |  70.11    |  2.171    |  9.982    |  1.823e+0 |
|  67       |  0.5523   |  21.21    |  57.52    |  2.531    |  3.489    |  2.197e+0 |
|  68       |  0.5543   |  59.34    |  72.61    |  2.339    |  9.275    |  2.99e+03 |
|  69       |  0.5569   |  20.21    |  70.05    |  2.5

In [236]:
print(RF_BO.max)

{'target': 0.5580876217782031, 'params': {'max_depth': 58.27964410292753, 'max_features': 72.21621678082809, 'min_samples_leaf': 2.9702729146179276, 'min_samples_split': 6.749725970412703, 'n_estimators': 1000.6965080366958}}


In [242]:
params = {'bootstrap': False, 
          'max_depth': int(RF_BO.max['params']['max_depth']), 
          'max_features': int(RF_BO.max['params']['max_features']), 
          'min_samples_leaf': int(RF_BO.max['params']['min_samples_leaf']), 
          'min_samples_split': int(RF_BO.max['params']['min_samples_split']), 
          'n_estimators': int(RF_BO.max['params']['n_estimators'])}

rf = RandomForestClassifier(**params)
#rf = RandomForestClassifier(bootstrap = False, max_depth = int(RF_BO.max['params']['max_depth']), 
#                            max_features = int(RF_BO.max['params']['max_features']), 
#                            min_samples_leaf = int(RF_BO.max['params']['min_samples_leaf']), 
#                            min_samples_split = int(RF_BO.max['params']['min_samples_split']), 
#                            n_estimators = int(RF_BO.max['params']['n_estimators']), n_jobs = -1)

rf.fit(X_train_with_cats, y_train)

rf_pred_y = rf.predict(X_valid_with_cats)

print('Train accuracy score:',qwk3(y_train, rf.predict(X_train_with_cats)))
print('Test accuracy score:', qwk3(y_valid,rf_pred_y))

# 0.5523468488732437

Train accuracy score: 0.9943584423691794
Test accuracy score: 0.5523468488732437


In [320]:
del RF_BO, bounds_RF
gc.collect()

NameError: name 'RF_BO' is not defined

In [249]:
# K Nearest
from sklearn.neighbors import KNeighborsClassifier
def KNN_Bayesian(n_neighbors, weights, algorithm, leaf_size, p):
    
    if weights >= 0 and weights < 1.0:
        weights = 'uniform'
    else:
        weights = 'distance'
        
    if algorithm >= 0 and algorithm < 1.0:
        algorithm = 'ball_tree'
    elif algorithm >= 1 and algorithm < 2.0:
        algorithm = 'kd_tree'
    elif algorithm >= 2 and algorithm < 3.0:
        algorithm = 'brute'
    else:
        algorithm = 'auto'
    
    params = {
        'n_neighbors': int(n_neighbors),
        'weights': weights,
        'algorithm': algorithm,
        'leaf_size': int(leaf_size),
        'p': int(p),
        'n_jobs': -1
    }
    
    model = KNeighborsClassifier(**params)
    model.fit(X_train_with_cats, y_train)
    pred = model.predict(X_valid_with_cats)
    
    return qwk3(y_valid, pred)

In [250]:
init_points = 25
n_iter = 50

bounds_KNN = {
         'n_neighbors': (5, 25),
        'weights': (0, 2),
        'algorithm': (0, 4),
        'leaf_size': (10, 40),
        'p': (1, 2.99)
}

KNN_BO = BayesianOptimization(KNN_Bayesian, bounds_KNN, random_state=1029)

with warnings.catch_warnings():
    warnings.filterwarnings('ignore')
    KNN_BO.maximize(init_points=init_points, n_iter=n_iter, acq='ucb', xi=0.0, alpha=1e-6)

|   iter    |  target   | algorithm | leaf_size | n_neig... |     p     |  weights  |
-------------------------------------------------------------------------------------
|  1        |  0.4852   |  0.1642   |  22.29    |  16.77    |  2.791    |  0.2422   |
|  2        |  0.4605   |  0.6808   |  38.21    |  16.91    |  1.668    |  0.8834   |
|  3        |  0.4888   |  1.983    |  12.64    |  10.48    |  2.313    |  0.1607   |
|  4        |  0.4882   |  0.1546   |  30.25    |  8.747    |  2.869    |  1.742    |
|  5        |  0.4544   |  1.433    |  27.04    |  22.59    |  1.9      |  1.41     |
|  6        |  0.4913   |  3.185    |  38.31    |  11.08    |  2.81     |  1.0      |
|  7        |  0.4246   |  0.1552   |  18.02    |  7.328    |  1.565    |  0.9809   |
|  8        |  0.486    |  3.029    |  31.21    |  15.56    |  2.732    |  0.04598  |
|  9        |  0.4871   |  1.233    |  15.05    |  13.52    |  2.546    |  1.069    |
|  10       |  0.4505   |  1.166    |  24.14    |  18.

|  58       |  0.4912   |  3.853    |  10.0     |  22.22    |  2.968    |  1.675    |
|  59       |  0.4903   |  0.213    |  21.51    |  12.43    |  2.931    |  1.997    |
|  60       |  0.4864   |  2.685    |  10.05    |  21.5     |  2.968    |  0.03958  |
|  61       |  0.4894   |  4.0      |  10.0     |  25.0     |  2.99     |  0.6675   |
|  62       |  0.4879   |  4.0      |  12.69    |  25.0     |  2.99     |  1.945    |
|  63       |  0.4892   |  3.248    |  10.1     |  11.26    |  2.879    |  0.001715 |
|  64       |  0.4922   |  2.381    |  39.67    |  18.34    |  2.953    |  0.1462   |
|  65       |  0.489    |  0.09658  |  31.59    |  24.88    |  2.929    |  0.1597   |
|  66       |  0.4906   |  2.669    |  13.75    |  17.81    |  2.965    |  1.971    |
|  67       |  0.4874   |  2.952    |  14.73    |  8.282    |  2.971    |  0.005954 |
|  68       |  0.4937   |  0.04441  |  29.7     |  19.54    |  2.986    |  0.3491   |
|  69       |  0.4643   |  2.546    |  13.38    |  15.

In [251]:
print(KNN_BO.max)

{'target': 0.49368862461105056, 'params': {'algorithm': 0.04441288498288465, 'leaf_size': 29.702070879545722, 'n_neighbors': 19.544302888065488, 'p': 2.986361352754792, 'weights': 0.3491139618762451}}


In [257]:
weights = KNN_BO.max['params']['weights']
if weights >= 0 and weights < 1.0:
    weights = 'uniform'
else:
    weights = 'distance'

algorithm = KNN_BO.max['params']['algorithm']
if algorithm >= 0 and algorithm < 1.0:
    algorithm = 'ball_tree'
elif algorithm >= 1 and algorithm < 2.0:
    algorithm = 'kd_tree'
elif algorithm >= 2 and algorithm < 3.0:
    algorithm = 'brute'
else:
    algorithm = 'auto'

params = {
         'n_neighbors': int(KNN_BO.max['params']['n_neighbors']),
        'weights': weights,
        'algorithm': algorithm,
        'leaf_size': int(KNN_BO.max['params']['leaf_size']),
        'p': int(KNN_BO.max['params']['p']),
        'n_jobs': -1
}
knn = KNeighborsClassifier(**params)

#Fit the model
knn_model = knn.fit(X_train_with_cats, y_train)

knn_pred_y = knn_model.predict(X_valid_with_cats)
print('Train accuracy score:',qwk3(y_train,knn_model.predict(X_train_with_cats)))
print('Test accuracy score:',qwk3(y_valid,knn_pred_y))

# 0.4942484678835759

Train accuracy score: 0.5033603839532681
Test accuracy score: 0.49368862461105056


In [321]:
del KNN_BO, bounds_KNN
gc.collect()

3624

In [274]:
# XG Boost
import xgboost as xgb
def XGB_Bayesian(colsample_bytree, 
                 learning_rate, 
                 max_depth, 
                 subsample, 
                 min_child_weight, 
                 gamma, 
                 n_estimators, 
                 num_rounds):
      
    params = {'colsample_bytree': colsample_bytree,                 
            'learning_rate': learning_rate,
            'max_depth': int(max_depth),
            'subsample': subsample,
            'min_child_weight': int(min_child_weight),
            'gamma':gamma,
            'n_estimators':int(n_estimators),
            'verbosity': 0
             }
    
    xg_train = xgb.DMatrix(X_train_with_cats, label=y_train)
    xg_test = xgb.DMatrix(X_valid_with_cats, label=y_valid)
    xg_train.save_binary('train.buffer')
    xg_test.save_binary('test.buffer')
    watchlist = [(xg_train, 'train'), (xg_test, 'test')]
    num_round = int(num_rounds)
    bst = xgb.train(params, xg_train, num_round, watchlist)
    bst_pred = bst.predict(xg_test)
    bst_pred = get_class_pred(bst_pred, reduce_train)
    
    return qwk3(y_valid, bst_pred)

In [280]:
init_points = 25
n_iter = 50

bounds_XGB = {'colsample_bytree': (0.1, 0.3),                 
            'learning_rate': (0.01, 0.02),
            'max_depth': (5, 7),
            'subsample': (0.5, 1),
            'min_child_weight':(2, 4),
            'gamma': (0.1, 0.3),
            'n_estimators': (1200, 2000),
            'num_rounds': (600, 800)
         }

XGB_BO = BayesianOptimization(XGB_Bayesian, bounds_XGB, random_state=1029)

with warnings.catch_warnings():
    warnings.filterwarnings('ignore')
    XGB_BO.maximize(init_points=init_points, n_iter=n_iter, acq='ucb', xi=0.0, alpha=1e-6)

|   iter    |  target   | colsam... |   gamma   | learni... | max_depth | min_ch... | n_esti... | num_ro... | subsample |
-------------------------------------------------------------------------------------------------------------------------
[0]	train-merror:0.380441	test-merror:0.490296
[1]	train-merror:0.366874	test-merror:0.476164
[2]	train-merror:0.338367	test-merror:0.433201
[3]	train-merror:0.333603	test-merror:0.433767
[4]	train-merror:0.333683	test-merror:0.431317
[5]	train-merror:0.334975	test-merror:0.431694
[6]	train-merror:0.328676	test-merror:0.425853
[7]	train-merror:0.320601	test-merror:0.41662
[8]	train-merror:0.324558	test-merror:0.419634
[9]	train-merror:0.316321	test-merror:0.414735
[10]	train-merror:0.31301	test-merror:0.41059
[11]	train-merror:0.31196	test-merror:0.41059
[12]	train-merror:0.310506	test-merror:0.410401
[13]	train-merror:0.307841	test-merror:0.410213
[14]	train-merror:0.307438	test-merror:0.41172
[15]	train-merror:0.305257	test-merror:0.41172
[16]	

[166]	train-merror:0.053945	test-merror:0.386848
[167]	train-merror:0.052653	test-merror:0.387413
[168]	train-merror:0.051603	test-merror:0.38779
[169]	train-merror:0.051199	test-merror:0.387036
[170]	train-merror:0.050311	test-merror:0.386471
[171]	train-merror:0.049423	test-merror:0.387036
[172]	train-merror:0.04918	test-merror:0.387036
[173]	train-merror:0.049019	test-merror:0.386848
[174]	train-merror:0.04805	test-merror:0.386659
[175]	train-merror:0.047242	test-merror:0.386282
[176]	train-merror:0.046515	test-merror:0.385905
[177]	train-merror:0.045789	test-merror:0.386471
[178]	train-merror:0.045304	test-merror:0.386094
[179]	train-merror:0.0449	test-merror:0.38534
[180]	train-merror:0.0449	test-merror:0.384775
[181]	train-merror:0.043608	test-merror:0.385905
[182]	train-merror:0.043366	test-merror:0.38534
[183]	train-merror:0.042639	test-merror:0.385529
[184]	train-merror:0.042155	test-merror:0.385529
[185]	train-merror:0.041509	test-merror:0.385905
[186]	train-merror:0.040862	t

[335]	train-merror:0.010337	test-merror:0.385717
[336]	train-merror:0.010337	test-merror:0.384775
[337]	train-merror:0.010337	test-merror:0.385152
[338]	train-merror:0.010175	test-merror:0.384775
[339]	train-merror:0.010014	test-merror:0.38534
[340]	train-merror:0.009933	test-merror:0.385717
[341]	train-merror:0.009852	test-merror:0.385717
[342]	train-merror:0.009691	test-merror:0.385529
[343]	train-merror:0.009691	test-merror:0.384586
[344]	train-merror:0.009529	test-merror:0.384775
[345]	train-merror:0.009448	test-merror:0.384775
[346]	train-merror:0.009448	test-merror:0.385152
[347]	train-merror:0.009206	test-merror:0.38534
[348]	train-merror:0.009125	test-merror:0.384775
[349]	train-merror:0.009125	test-merror:0.384963
[350]	train-merror:0.009045	test-merror:0.384398
[351]	train-merror:0.009045	test-merror:0.38421
[352]	train-merror:0.008964	test-merror:0.384586
[353]	train-merror:0.008883	test-merror:0.38421
[354]	train-merror:0.008964	test-merror:0.384586
[355]	train-merror:0.008

[503]	train-merror:0.004684	test-merror:0.385717
[504]	train-merror:0.004684	test-merror:0.384963
[505]	train-merror:0.004684	test-merror:0.384775
[506]	train-merror:0.004765	test-merror:0.384586
[507]	train-merror:0.004765	test-merror:0.384963
[508]	train-merror:0.004684	test-merror:0.385152
[509]	train-merror:0.004603	test-merror:0.384963
[510]	train-merror:0.004522	test-merror:0.384775
[511]	train-merror:0.004522	test-merror:0.38534
[512]	train-merror:0.004522	test-merror:0.384775
[513]	train-merror:0.004522	test-merror:0.385529
[514]	train-merror:0.004522	test-merror:0.386094
[515]	train-merror:0.004522	test-merror:0.385529
[516]	train-merror:0.004522	test-merror:0.38534
[517]	train-merror:0.004522	test-merror:0.384775
[518]	train-merror:0.004522	test-merror:0.384775
[519]	train-merror:0.004522	test-merror:0.384963
[520]	train-merror:0.004522	test-merror:0.38534
[521]	train-merror:0.004522	test-merror:0.384963
[522]	train-merror:0.004522	test-merror:0.385152
[523]	train-merror:0.00

[672]	train-merror:0.003634	test-merror:0.382891
[673]	train-merror:0.003634	test-merror:0.383079
[674]	train-merror:0.003634	test-merror:0.383267
[675]	train-merror:0.003634	test-merror:0.383644
[676]	train-merror:0.003634	test-merror:0.383833
[677]	train-merror:0.003634	test-merror:0.383833
[678]	train-merror:0.003634	test-merror:0.383833
[679]	train-merror:0.003634	test-merror:0.383456
[680]	train-merror:0.003634	test-merror:0.383644
[681]	train-merror:0.003634	test-merror:0.383267
[682]	train-merror:0.003634	test-merror:0.383833
[683]	train-merror:0.003634	test-merror:0.383079
[684]	train-merror:0.003634	test-merror:0.383267
[685]	train-merror:0.003634	test-merror:0.383079
[686]	train-merror:0.003634	test-merror:0.383267
[687]	train-merror:0.003634	test-merror:0.383079
[688]	train-merror:0.003634	test-merror:0.383267
[689]	train-merror:0.003634	test-merror:0.382891
[690]	train-merror:0.003634	test-merror:0.383267
[691]	train-merror:0.003634	test-merror:0.382514
[692]	train-merror:0

...

[359]	train-merror:0.01599	test-merror:0.392877
[360]	train-merror:0.01607	test-merror:0.393254
[361]	train-merror:0.015909	test-merror:0.394196
[362]	train-merror:0.015828	test-merror:0.392877
[363]	train-merror:0.01599	test-merror:0.393066
[364]	train-merror:0.015828	test-merror:0.393819
[365]	train-merror:0.015747	test-merror:0.392689
[366]	train-merror:0.015424	test-merror:0.393066
[367]	train-merror:0.015101	test-merror:0.393254
[368]	train-merror:0.015021	test-merror:0.393631
[369]	train-merror:0.015182	test-merror:0.394573
[370]	train-merror:0.014617	test-merror:0.394573
[371]	train-merror:0.014617	test-merror:0.394196
[372]	train-merror:0.014698	test-merror:0.393819
[373]	train-merror:0.014778	test-merror:0.392877
[374]	train-merror:0.014617	test-merror:0.393066
[375]	train-merror:0.014294	test-merror:0.393819
[376]	train-merror:0.014375	test-merror:0.392689
[377]	train-merror:0.014052	test-merror:0.394008
[378]	train-merror:0.01389	test-merror:0.393443
[379]	train-merror:0.014

[527]	train-merror:0.00743	test-merror:0.396458
[528]	train-merror:0.00751	test-merror:0.397211
[529]	train-merror:0.007349	test-merror:0.397023
[530]	train-merror:0.007268	test-merror:0.39853
[531]	train-merror:0.007268	test-merror:0.398719
[532]	train-merror:0.007349	test-merror:0.399096
[533]	train-merror:0.007268	test-merror:0.398719
[534]	train-merror:0.007187	test-merror:0.39853
[535]	train-merror:0.007107	test-merror:0.398153
[536]	train-merror:0.007268	test-merror:0.39853
[537]	train-merror:0.007107	test-merror:0.398719
[538]	train-merror:0.007107	test-merror:0.399096
[539]	train-merror:0.007268	test-merror:0.398719
[540]	train-merror:0.007107	test-merror:0.398153
[541]	train-merror:0.007026	test-merror:0.397965
[542]	train-merror:0.007026	test-merror:0.398907
[543]	train-merror:0.007026	test-merror:0.399661
[544]	train-merror:0.007107	test-merror:0.398719
[545]	train-merror:0.007187	test-merror:0.398342
[546]	train-merror:0.007349	test-merror:0.398719
[547]	train-merror:0.0073

[695]	train-merror:0.005653	test-merror:0.400603
[696]	train-merror:0.005653	test-merror:0.400603
[697]	train-merror:0.005734	test-merror:0.400791
[698]	train-merror:0.005653	test-merror:0.401734
[699]	train-merror:0.005653	test-merror:0.40098
[700]	train-merror:0.005895	test-merror:0.401545
[701]	train-merror:0.005734	test-merror:0.402299
[702]	train-merror:0.005491	test-merror:0.401357
[703]	train-merror:0.005572	test-merror:0.401734
[704]	train-merror:0.005572	test-merror:0.401734
[705]	train-merror:0.005491	test-merror:0.401545
[706]	train-merror:0.005572	test-merror:0.402299
[707]	train-merror:0.005734	test-merror:0.402864
[708]	train-merror:0.005814	test-merror:0.401922
[709]	train-merror:0.005491	test-merror:0.401922
[710]	train-merror:0.005653	test-merror:0.401922
|  34       |  0.4221   |  1.0      |  0.5      |  0.1      |  10.0     |  9.0      |  1.113e+0 |  711.2    |  0.5      |
[0]	train-merror:0.315352	test-merror:0.402676
[1]	train-merror:0.315352	test-merror:0.40098
[2

[151]	train-merror:0.252604	test-merror:0.382325
[152]	train-merror:0.251878	test-merror:0.382891
[153]	train-merror:0.25212	test-merror:0.382514
[154]	train-merror:0.251958	test-merror:0.382514
[155]	train-merror:0.251716	test-merror:0.382702
[156]	train-merror:0.251312	test-merror:0.382137
[157]	train-merror:0.250828	test-merror:0.382702
[158]	train-merror:0.250585	test-merror:0.38176
[159]	train-merror:0.250424	test-merror:0.381948
[160]	train-merror:0.250262	test-merror:0.382702
[161]	train-merror:0.250262	test-merror:0.382514
[162]	train-merror:0.25002	test-merror:0.381572
[163]	train-merror:0.249697	test-merror:0.381572
[164]	train-merror:0.24897	test-merror:0.381572
[165]	train-merror:0.248647	test-merror:0.381383
[166]	train-merror:0.24889	test-merror:0.381006
[167]	train-merror:0.248647	test-merror:0.381195
[168]	train-merror:0.248082	test-merror:0.380441
[169]	train-merror:0.248082	test-merror:0.380629
[170]	train-merror:0.247759	test-merror:0.381006
[171]	train-merror:0.2480

KeyboardInterrupt: 

In [322]:
print(XGB_BO.max)

{'target': 0.46243980441859467, 'params': {'colsample_bytree': 0.9225042432318004, 'gamma': 0.2242528660097748, 'learning_rate': 0.05286219593431703, 'max_depth': 9.655939905529312, 'min_child_weight': 7.855233989636829, 'n_estimators': 1055.0105494089557, 'num_rounds': 793.281917089737, 'subsample': 0.9777047883118943}}


In [281]:
params = {'colsample_bytree': XGB_BO.max['params']['colsample_bytree'],                 
            'learning_rate': XGB_BO.max['params']['learning_rate'],
            'max_depth': int(XGB_BO.max['params']['max_depth']),
            'subsample': XGB_BO.max['params']['subsample'],
            'min_child_weight': int(XGB_BO.max['params']['min_child_weight']),
            'gamma': XGB_BO.max['params']['gamma'],
            'n_estimators': int(XGB_BO.max['params']['n_estimators'])
         }

xg_train = xgb.DMatrix(X_train_with_cats, label=y_train)
xg_test = xgb.DMatrix(X_valid_with_cats, label=y_valid)
xg_train.save_binary('train.buffer')
xg_test.save_binary('test.buffer')
watchlist = [(xg_train, 'train'), (xg_test, 'test')]
num_round = int(XGB_BO.max['params']['num_rounds'])
bst = xgb.train(params, xg_train, num_round, watchlist)

[0]	train-rmse:1.8597	test-rmse:1.85784
[1]	train-rmse:1.84721	test-rmse:1.84551
[2]	train-rmse:1.83576	test-rmse:1.8342
[3]	train-rmse:1.82489	test-rmse:1.82345
[4]	train-rmse:1.81381	test-rmse:1.81261
[5]	train-rmse:1.80204	test-rmse:1.80104
[6]	train-rmse:1.79026	test-rmse:1.78953
[7]	train-rmse:1.7797	test-rmse:1.77938
[8]	train-rmse:1.76932	test-rmse:1.76988
[9]	train-rmse:1.7582	test-rmse:1.7591
[10]	train-rmse:1.74804	test-rmse:1.74906
[11]	train-rmse:1.73773	test-rmse:1.73913
[12]	train-rmse:1.72778	test-rmse:1.72938
[13]	train-rmse:1.71749	test-rmse:1.71942
[14]	train-rmse:1.7077	test-rmse:1.70995
[15]	train-rmse:1.69818	test-rmse:1.70073
[16]	train-rmse:1.6874	test-rmse:1.69072
[17]	train-rmse:1.67773	test-rmse:1.6813
[18]	train-rmse:1.66819	test-rmse:1.67254
[19]	train-rmse:1.6583	test-rmse:1.66285
[20]	train-rmse:1.64967	test-rmse:1.65449
[21]	train-rmse:1.64036	test-rmse:1.64532
[22]	train-rmse:1.63143	test-rmse:1.63657
[23]	train-rmse:1.62292	test-rmse:1.62844
[24]	train-

[195]	train-rmse:1.01379	test-rmse:1.07366
[196]	train-rmse:1.01232	test-rmse:1.07259
[197]	train-rmse:1.01146	test-rmse:1.07202
[198]	train-rmse:1.01062	test-rmse:1.07144
[199]	train-rmse:1.00981	test-rmse:1.07086
[200]	train-rmse:1.00872	test-rmse:1.06998
[201]	train-rmse:1.00747	test-rmse:1.06901
[202]	train-rmse:1.00679	test-rmse:1.06856
[203]	train-rmse:1.00599	test-rmse:1.06827
[204]	train-rmse:1.00462	test-rmse:1.06719
[205]	train-rmse:1.00358	test-rmse:1.0663
[206]	train-rmse:1.00263	test-rmse:1.06573
[207]	train-rmse:1.00131	test-rmse:1.06485
[208]	train-rmse:1.00057	test-rmse:1.06432
[209]	train-rmse:0.999585	test-rmse:1.0636
[210]	train-rmse:0.998675	test-rmse:1.06291
[211]	train-rmse:0.998	test-rmse:1.06246
[212]	train-rmse:0.997171	test-rmse:1.06186
[213]	train-rmse:0.996325	test-rmse:1.06129
[214]	train-rmse:0.995047	test-rmse:1.06034
[215]	train-rmse:0.994427	test-rmse:1.05997
[216]	train-rmse:0.993781	test-rmse:1.0596
[217]	train-rmse:0.992498	test-rmse:1.05867
[218]	tr

[383]	train-rmse:0.896937	test-rmse:1.00454
[384]	train-rmse:0.896481	test-rmse:1.00435
[385]	train-rmse:0.896096	test-rmse:1.00432
[386]	train-rmse:0.895843	test-rmse:1.00426
[387]	train-rmse:0.895265	test-rmse:1.00397
[388]	train-rmse:0.894849	test-rmse:1.00389
[389]	train-rmse:0.894309	test-rmse:1.00359
[390]	train-rmse:0.893943	test-rmse:1.00348
[391]	train-rmse:0.893643	test-rmse:1.00337
[392]	train-rmse:0.893213	test-rmse:1.00312
[393]	train-rmse:0.892767	test-rmse:1.00284
[394]	train-rmse:0.892383	test-rmse:1.00269
[395]	train-rmse:0.891901	test-rmse:1.0024
[396]	train-rmse:0.891575	test-rmse:1.00235
[397]	train-rmse:0.891193	test-rmse:1.00213
[398]	train-rmse:0.890532	test-rmse:1.00173
[399]	train-rmse:0.890065	test-rmse:1.00147
[400]	train-rmse:0.889626	test-rmse:1.00127
[401]	train-rmse:0.889326	test-rmse:1.00124
[402]	train-rmse:0.888977	test-rmse:1.0011
[403]	train-rmse:0.888615	test-rmse:1.00104
[404]	train-rmse:0.88803	test-rmse:1.0007
[405]	train-rmse:0.887671	test-rmse:

[567]	train-rmse:0.837961	test-rmse:0.983953
[568]	train-rmse:0.837728	test-rmse:0.983912
[569]	train-rmse:0.837483	test-rmse:0.983898
[570]	train-rmse:0.837061	test-rmse:0.983685
[571]	train-rmse:0.836951	test-rmse:0.983707
[572]	train-rmse:0.836778	test-rmse:0.983714
[573]	train-rmse:0.83637	test-rmse:0.983561
[574]	train-rmse:0.836019	test-rmse:0.983435
[575]	train-rmse:0.835827	test-rmse:0.983419
[576]	train-rmse:0.835558	test-rmse:0.983349
[577]	train-rmse:0.835474	test-rmse:0.983347
[578]	train-rmse:0.835215	test-rmse:0.983323
[579]	train-rmse:0.834963	test-rmse:0.983272
[580]	train-rmse:0.834749	test-rmse:0.983249
[581]	train-rmse:0.834373	test-rmse:0.983105
[582]	train-rmse:0.834255	test-rmse:0.98309
[583]	train-rmse:0.834018	test-rmse:0.983072
[584]	train-rmse:0.833831	test-rmse:0.983008
[585]	train-rmse:0.833545	test-rmse:0.982953
[586]	train-rmse:0.833372	test-rmse:0.982943
[587]	train-rmse:0.833188	test-rmse:0.982884
[588]	train-rmse:0.832843	test-rmse:0.982773
[589]	train-

In [318]:
bst_pred = bst.predict(xg_test)
bst_pred_y = get_class_pred(bst_pred, reduce_train)
bst_train_pred = get_class_pred(bst.predict(xg_train), reduce_train)

print('Train accuracy score:',qwk3(y_train,bst_train_pred))
print('Test accuracy score:',qwk3(y_valid,bst_pred_y))

# 0.6060568482704531

ValueError: feature_names mismatch: ['Clip', 'Activity', 'Assessment', 'Game', 'acc_Bird Measurer (Assessment)', 'acc_Cauldron Filler (Assessment)', 'acc_Chest Sorter (Assessment)', 'acc_Mushroom Sorter (Assessment)', '2050', '4100', '2060', '4110', '2070', '2075', '2080', '2081', '2083', '3110', '3120', '3121', '4220', '4230', '5000', '4010', '4020', '4021', '4022', '4025', '4030', '4031', '4035', '4040', '4045', '2000', '4050', '2010', '2020', '4070', '2025', '4080', '2035', '4090', '4095', 'Tree Top City - Level 2', 'Crystal Caves - Level 3', 'Bug Measurer (Activity)', 'Balancing Act', 'Rulers', 'Dino Drink', 'Leaf Leader', 'Tree Top City - Level 1', 'Tree Top City - Level 3', 'Flower Waterer (Activity)', 'Lifting Heavy Things', 'Sandcastle Builder (Activity)', 'Chow Time', 'Pan Balance', 'Honey Cake', 'Happy Camel', 'Cart Balancer (Assessment)', 'Chicken Balancer (Activity)', 'Chest Sorter (Assessment)', 'Crystals Rule', 'All Star Sorting', 'Mushroom Sorter (Assessment)', 'Ordering

In [323]:
del XGB_BO, bounds_XGB
gc.collect()

NameError: name 'bounds_XGB' is not defined

In [283]:
from catboost import CatBoostRegressor, CatBoostClassifier

# Create a based model
cat = CatBoostRegressor(loss_function='MultiRMSE', task_type='CPU', #classes_count=4, 
                        iterations=1860, learning_rate=0.04, random_seed=0, bootstrap_type='Bayesian', 
                        bagging_temperature=1, depth=6, l2_leaf_reg=2, rsm = 1, logging_level='Verbose')

#cat = CatBoostClassifier(loss_function='MultiClass', task_type='CPU', classes_count=4, 
#                        iterations=1860, learning_rate=0.04, random_seed=0, bootstrap_type='Bayesian', 
#                        bagging_temperature=1, depth=6, l2_leaf_reg=2, rsm = 1, logging_level='Verbose', 
#                        class_weights=[0.9,2.3,3.1,0.75])

# Fit
cat.fit(X_train_with_cats, y_train, verbose=True)

0:	learn: 2.2035617	total: 19.6ms	remaining: 36.5s
1:	learn: 2.1401646	total: 35.6ms	remaining: 33s
2:	learn: 2.0799515	total: 52ms	remaining: 32.2s
3:	learn: 2.0225095	total: 67.7ms	remaining: 31.4s
4:	learn: 1.9686771	total: 84.2ms	remaining: 31.2s
5:	learn: 1.9151206	total: 101ms	remaining: 31.1s
6:	learn: 1.8634762	total: 119ms	remaining: 31.5s
7:	learn: 1.8166664	total: 135ms	remaining: 31.2s
8:	learn: 1.7726770	total: 152ms	remaining: 31.2s
9:	learn: 1.7280686	total: 169ms	remaining: 31.2s
10:	learn: 1.6870817	total: 186ms	remaining: 31.2s
11:	learn: 1.6470708	total: 204ms	remaining: 31.3s
12:	learn: 1.6097113	total: 224ms	remaining: 31.9s
13:	learn: 1.5792262	total: 242ms	remaining: 31.9s
14:	learn: 1.5448366	total: 260ms	remaining: 32s
15:	learn: 1.5153976	total: 278ms	remaining: 32.1s
16:	learn: 1.4855110	total: 298ms	remaining: 32.3s
17:	learn: 1.4569379	total: 319ms	remaining: 32.6s
18:	learn: 1.4325260	total: 337ms	remaining: 32.7s
19:	learn: 1.4085061	total: 356ms	remainin

166:	learn: 0.9827596	total: 3.26s	remaining: 33.1s
167:	learn: 0.9823267	total: 3.29s	remaining: 33.1s
168:	learn: 0.9819951	total: 3.31s	remaining: 33.1s
169:	learn: 0.9815846	total: 3.32s	remaining: 33s
170:	learn: 0.9812151	total: 3.35s	remaining: 33s
171:	learn: 0.9806717	total: 3.37s	remaining: 33s
172:	learn: 0.9803986	total: 3.38s	remaining: 33s
173:	learn: 0.9800513	total: 3.4s	remaining: 33s
174:	learn: 0.9797476	total: 3.42s	remaining: 33s
175:	learn: 0.9793997	total: 3.45s	remaining: 33s
176:	learn: 0.9790203	total: 3.47s	remaining: 33s
177:	learn: 0.9784200	total: 3.49s	remaining: 33s
178:	learn: 0.9781658	total: 3.51s	remaining: 33s
179:	learn: 0.9779380	total: 3.53s	remaining: 32.9s
180:	learn: 0.9776034	total: 3.55s	remaining: 32.9s
181:	learn: 0.9772778	total: 3.57s	remaining: 32.9s
182:	learn: 0.9769660	total: 3.59s	remaining: 32.9s
183:	learn: 0.9766932	total: 3.61s	remaining: 32.9s
184:	learn: 0.9766163	total: 3.64s	remaining: 33s
185:	learn: 0.9763288	total: 3.66s	

328:	learn: 0.9375354	total: 6.58s	remaining: 30.6s
329:	learn: 0.9372666	total: 6.61s	remaining: 30.6s
330:	learn: 0.9370564	total: 6.62s	remaining: 30.6s
331:	learn: 0.9368431	total: 6.64s	remaining: 30.6s
332:	learn: 0.9366272	total: 6.66s	remaining: 30.6s
333:	learn: 0.9364593	total: 6.68s	remaining: 30.5s
334:	learn: 0.9363390	total: 6.7s	remaining: 30.5s
335:	learn: 0.9361148	total: 6.72s	remaining: 30.5s
336:	learn: 0.9357437	total: 6.74s	remaining: 30.5s
337:	learn: 0.9356497	total: 6.76s	remaining: 30.4s
338:	learn: 0.9354257	total: 6.78s	remaining: 30.4s
339:	learn: 0.9350593	total: 6.81s	remaining: 30.4s
340:	learn: 0.9348386	total: 6.83s	remaining: 30.4s
341:	learn: 0.9345342	total: 6.84s	remaining: 30.4s
342:	learn: 0.9343399	total: 6.86s	remaining: 30.4s
343:	learn: 0.9342315	total: 6.88s	remaining: 30.3s
344:	learn: 0.9339621	total: 6.9s	remaining: 30.3s
345:	learn: 0.9337262	total: 6.92s	remaining: 30.3s
346:	learn: 0.9335109	total: 6.94s	remaining: 30.3s
347:	learn: 0.

495:	learn: 0.9025001	total: 9.92s	remaining: 27.3s
496:	learn: 0.9022626	total: 9.94s	remaining: 27.3s
497:	learn: 0.9020490	total: 9.97s	remaining: 27.3s
498:	learn: 0.9018419	total: 9.98s	remaining: 27.2s
499:	learn: 0.9017175	total: 10s	remaining: 27.2s
500:	learn: 0.9015728	total: 10s	remaining: 27.2s
501:	learn: 0.9013507	total: 10s	remaining: 27.2s
502:	learn: 0.9010723	total: 10.1s	remaining: 27.2s
503:	learn: 0.9009094	total: 10.1s	remaining: 27.2s
504:	learn: 0.9007374	total: 10.1s	remaining: 27.1s
505:	learn: 0.9005682	total: 10.1s	remaining: 27.1s
506:	learn: 0.9003966	total: 10.2s	remaining: 27.1s
507:	learn: 0.9001741	total: 10.2s	remaining: 27.1s
508:	learn: 0.9000129	total: 10.2s	remaining: 27.1s
509:	learn: 0.8999044	total: 10.2s	remaining: 27s
510:	learn: 0.8997463	total: 10.2s	remaining: 27s
511:	learn: 0.8996201	total: 10.3s	remaining: 27s
512:	learn: 0.8995330	total: 10.3s	remaining: 27s
513:	learn: 0.8992715	total: 10.3s	remaining: 27s
514:	learn: 0.8991428	total:

656:	learn: 0.8767646	total: 13.2s	remaining: 24.2s
657:	learn: 0.8765996	total: 13.3s	remaining: 24.2s
658:	learn: 0.8764564	total: 13.3s	remaining: 24.2s
659:	learn: 0.8763570	total: 13.3s	remaining: 24.2s
660:	learn: 0.8761095	total: 13.3s	remaining: 24.2s
661:	learn: 0.8759793	total: 13.3s	remaining: 24.1s
662:	learn: 0.8758448	total: 13.4s	remaining: 24.1s
663:	learn: 0.8757290	total: 13.4s	remaining: 24.1s
664:	learn: 0.8755756	total: 13.4s	remaining: 24.1s
665:	learn: 0.8754303	total: 13.4s	remaining: 24.1s
666:	learn: 0.8752422	total: 13.4s	remaining: 24.1s
667:	learn: 0.8749509	total: 13.5s	remaining: 24s
668:	learn: 0.8748784	total: 13.5s	remaining: 24s
669:	learn: 0.8747561	total: 13.5s	remaining: 24s
670:	learn: 0.8745789	total: 13.5s	remaining: 24s
671:	learn: 0.8744618	total: 13.5s	remaining: 23.9s
672:	learn: 0.8742759	total: 13.6s	remaining: 23.9s
673:	learn: 0.8741339	total: 13.6s	remaining: 23.9s
674:	learn: 0.8740733	total: 13.6s	remaining: 23.9s
675:	learn: 0.873950

...

1145:	learn: 0.8089653	total: 23.4s	remaining: 14.6s
1146:	learn: 0.8088650	total: 23.5s	remaining: 14.6s
1147:	learn: 0.8087687	total: 23.5s	remaining: 14.6s
1148:	learn: 0.8086646	total: 23.5s	remaining: 14.5s
1149:	learn: 0.8085573	total: 23.5s	remaining: 14.5s
1150:	learn: 0.8084612	total: 23.6s	remaining: 14.5s
1151:	learn: 0.8084073	total: 23.6s	remaining: 14.5s
1152:	learn: 0.8082733	total: 23.6s	remaining: 14.5s
1153:	learn: 0.8081627	total: 23.6s	remaining: 14.5s
1154:	learn: 0.8080905	total: 23.6s	remaining: 14.4s
1155:	learn: 0.8079369	total: 23.7s	remaining: 14.4s
1156:	learn: 0.8078926	total: 23.7s	remaining: 14.4s
1157:	learn: 0.8077990	total: 23.7s	remaining: 14.4s
1158:	learn: 0.8076600	total: 23.7s	remaining: 14.4s
1159:	learn: 0.8075777	total: 23.8s	remaining: 14.3s
1160:	learn: 0.8075597	total: 23.8s	remaining: 14.3s
1161:	learn: 0.8073272	total: 23.8s	remaining: 14.3s
1162:	learn: 0.8071405	total: 23.8s	remaining: 14.3s
1163:	learn: 0.8070587	total: 23.9s	remaining:

1302:	learn: 0.7913044	total: 26.8s	remaining: 11.5s
1303:	learn: 0.7912205	total: 26.8s	remaining: 11.4s
1304:	learn: 0.7911058	total: 26.8s	remaining: 11.4s
1305:	learn: 0.7910105	total: 26.9s	remaining: 11.4s
1306:	learn: 0.7908987	total: 26.9s	remaining: 11.4s
1307:	learn: 0.7907678	total: 26.9s	remaining: 11.4s
1308:	learn: 0.7906547	total: 26.9s	remaining: 11.3s
1309:	learn: 0.7904344	total: 26.9s	remaining: 11.3s
1310:	learn: 0.7902497	total: 27s	remaining: 11.3s
1311:	learn: 0.7901901	total: 27s	remaining: 11.3s
1312:	learn: 0.7900496	total: 27s	remaining: 11.3s
1313:	learn: 0.7898854	total: 27s	remaining: 11.2s
1314:	learn: 0.7897883	total: 27.1s	remaining: 11.2s
1315:	learn: 0.7896296	total: 27.1s	remaining: 11.2s
1316:	learn: 0.7895153	total: 27.1s	remaining: 11.2s
1317:	learn: 0.7894182	total: 27.1s	remaining: 11.2s
1318:	learn: 0.7892414	total: 27.2s	remaining: 11.1s
1319:	learn: 0.7891332	total: 27.2s	remaining: 11.1s
1320:	learn: 0.7890099	total: 27.2s	remaining: 11.1s
1

1463:	learn: 0.7729995	total: 30.4s	remaining: 8.21s
1464:	learn: 0.7728350	total: 30.4s	remaining: 8.19s
1465:	learn: 0.7727363	total: 30.4s	remaining: 8.17s
1466:	learn: 0.7726818	total: 30.4s	remaining: 8.15s
1467:	learn: 0.7725811	total: 30.4s	remaining: 8.13s
1468:	learn: 0.7724566	total: 30.5s	remaining: 8.11s
1469:	learn: 0.7723322	total: 30.5s	remaining: 8.09s
1470:	learn: 0.7722339	total: 30.5s	remaining: 8.07s
1471:	learn: 0.7721128	total: 30.5s	remaining: 8.05s
1472:	learn: 0.7719380	total: 30.6s	remaining: 8.03s
1473:	learn: 0.7718345	total: 30.6s	remaining: 8.01s
1474:	learn: 0.7716691	total: 30.6s	remaining: 7.99s
1475:	learn: 0.7715848	total: 30.6s	remaining: 7.97s
1476:	learn: 0.7715183	total: 30.7s	remaining: 7.95s
1477:	learn: 0.7714329	total: 30.7s	remaining: 7.93s
1478:	learn: 0.7713253	total: 30.7s	remaining: 7.91s
1479:	learn: 0.7712205	total: 30.7s	remaining: 7.89s
1480:	learn: 0.7711360	total: 30.8s	remaining: 7.87s
1481:	learn: 0.7710750	total: 30.8s	remaining:

1619:	learn: 0.7569156	total: 33.7s	remaining: 4.99s
1620:	learn: 0.7568220	total: 33.7s	remaining: 4.97s
1621:	learn: 0.7567801	total: 33.7s	remaining: 4.95s
1622:	learn: 0.7567148	total: 33.8s	remaining: 4.93s
1623:	learn: 0.7566089	total: 33.8s	remaining: 4.91s
1624:	learn: 0.7564890	total: 33.8s	remaining: 4.89s
1625:	learn: 0.7563991	total: 33.8s	remaining: 4.87s
1626:	learn: 0.7562334	total: 33.8s	remaining: 4.85s
1627:	learn: 0.7561202	total: 33.9s	remaining: 4.83s
1628:	learn: 0.7560741	total: 33.9s	remaining: 4.8s
1629:	learn: 0.7559086	total: 33.9s	remaining: 4.79s
1630:	learn: 0.7558108	total: 33.9s	remaining: 4.76s
1631:	learn: 0.7557478	total: 34s	remaining: 4.74s
1632:	learn: 0.7556137	total: 34s	remaining: 4.72s
1633:	learn: 0.7555231	total: 34s	remaining: 4.7s
1634:	learn: 0.7554558	total: 34s	remaining: 4.68s
1635:	learn: 0.7553240	total: 34s	remaining: 4.66s
1636:	learn: 0.7552209	total: 34.1s	remaining: 4.64s
1637:	learn: 0.7551099	total: 34.1s	remaining: 4.62s
1638:

1779:	learn: 0.7406202	total: 37.2s	remaining: 1.67s
1780:	learn: 0.7405064	total: 37.2s	remaining: 1.65s
1781:	learn: 0.7403956	total: 37.2s	remaining: 1.63s
1782:	learn: 0.7402864	total: 37.3s	remaining: 1.61s
1783:	learn: 0.7402257	total: 37.3s	remaining: 1.59s
1784:	learn: 0.7400827	total: 37.3s	remaining: 1.57s
1785:	learn: 0.7399990	total: 37.3s	remaining: 1.54s
1786:	learn: 0.7398589	total: 37.3s	remaining: 1.52s
1787:	learn: 0.7397786	total: 37.4s	remaining: 1.5s
1788:	learn: 0.7397255	total: 37.4s	remaining: 1.48s
1789:	learn: 0.7396431	total: 37.4s	remaining: 1.46s
1790:	learn: 0.7395763	total: 37.4s	remaining: 1.44s
1791:	learn: 0.7394923	total: 37.4s	remaining: 1.42s
1792:	learn: 0.7393510	total: 37.5s	remaining: 1.4s
1793:	learn: 0.7392486	total: 37.5s	remaining: 1.38s
1794:	learn: 0.7391512	total: 37.5s	remaining: 1.36s
1795:	learn: 0.7390896	total: 37.5s	remaining: 1.34s
1796:	learn: 0.7389366	total: 37.5s	remaining: 1.31s
1797:	learn: 0.7387612	total: 37.6s	remaining: 1

In [284]:
cat_pred = cat.predict(X_valid_with_cats)
cat_pred_y = get_class_pred(cat_pred, reduce_train)
cat_train_pred = get_class_pred(cat.predict(X_train_with_cats), reduce_train)

print('Train accuracy score:',qwk3(y_train,cat_train_pred))
print('Test accuracy score:',qwk3(y_valid,cat_pred_y))

# 0.6091561423979555

Train accuracy score: 0.8225382931358289
Test accuracy score: 0.6089249312801632


In [285]:
# Keras NN
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasClassifier
from keras.utils import np_utils
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.callbacks import EarlyStopping

# encode class values as integers
encoder = LabelEncoder()
encoder.fit(y_train)
encoded_Y = encoder.transform(y_train)
# convert integers to dummy variables (i.e. one hot encoded)
dummy_y = np_utils.to_categorical(encoded_Y)
encoder_valid = LabelEncoder()
encoder_valid.fit(y_train)
encoded_Y_valid = encoder.transform(y_valid)
# convert integers to dummy variables (i.e. one hot encoded)
dummy_y_valid = np_utils.to_categorical(encoded_Y_valid)

# define baseline model
def baseline_model():
    # create model
    model = Sequential()
    model.add(Dense(200, input_dim=X_train_with_cats.shape[1], activation='relu',kernel_initializer='random_normal'))
    model.add(Dense(100,activation='relu',kernel_initializer='random_normal'))
    model.add(Dense(50,activation='relu',kernel_initializer='random_normal'))
    model.add(Dense(25,activation='relu',kernel_initializer='random_normal'))
    model.add(Dense(4,activation='softmax',kernel_initializer='random_normal'))
    model.compile(loss='categorical_crossentropy', 
              optimizer='adam',
              metrics =['accuracy'])
    return model

model = KerasClassifier(build_fn=baseline_model)
monitor = EarlyStopping(monitor='val_loss', min_delta=1e-3, patience=20, 
                        verbose=1, mode='auto', restore_best_weights=True)
model.fit(X_train_with_cats,dummy_y,validation_data=(X_valid_with_cats,dummy_y_valid),callbacks=[monitor],verbose=2,epochs=1000)
#model.fit(X_train_with_cats, y_train)


Train on 12383 samples, validate on 5307 samples
Epoch 1/1000
 - 4s - loss: 1.1033 - accuracy: 0.5779 - val_loss: 1.0271 - val_accuracy: 0.6109
Epoch 2/1000
 - 4s - loss: 1.0278 - accuracy: 0.6133 - val_loss: 1.0119 - val_accuracy: 0.6141
Epoch 3/1000
 - 4s - loss: 1.0093 - accuracy: 0.6213 - val_loss: 1.0132 - val_accuracy: 0.6116
Epoch 4/1000
 - 4s - loss: 0.9960 - accuracy: 0.6230 - val_loss: 1.0063 - val_accuracy: 0.6158
Epoch 5/1000
 - 4s - loss: 0.9864 - accuracy: 0.6250 - val_loss: 0.9960 - val_accuracy: 0.6231
Epoch 6/1000
 - 4s - loss: 0.9721 - accuracy: 0.6324 - val_loss: 0.9938 - val_accuracy: 0.6199
Epoch 7/1000
 - 4s - loss: 0.9611 - accuracy: 0.6384 - val_loss: 0.9924 - val_accuracy: 0.6231
Epoch 8/1000
 - 4s - loss: 0.9484 - accuracy: 0.6407 - val_loss: 1.0003 - val_accuracy: 0.6194
Epoch 9/1000
 - 4s - loss: 0.9390 - accuracy: 0.6450 - val_loss: 1.0378 - val_accuracy: 0.6137
Epoch 10/1000
 - 4s - loss: 0.9275 - accuracy: 0.6486 - val_loss: 1.0385 - val_accuracy: 0.6139


In [286]:
nn_pred_y = model.predict(X_valid_with_cats)
nn_train_y = model.predict(X_train_with_cats)

print('Train accuracy score:',qwk3(y_train,nn_train_y))
print('Test accuracy score:',qwk3(y_valid,nn_pred_y))
# 0.5166242967865871

Train accuracy score: 0.5715748482858437
Test accuracy score: 0.5334244712431507


In [343]:
# LightGBM
import lightgbm as lgb
def LGB_Bayesian(n_estimators, 
                 subsample, 
                 subsample_freq, 
                 learning_rate, 
                 feature_fraction, 
                 max_depth, 
                 num_leaves,
                 min_data_in_leaf,
                 lambda_l1, 
                 lambda_l2,
                 early_stopping_rounds):
      
    params = {'n_estimators': int(n_estimators),
            'boosting_type': 'gbdt',
            'objective': 'regression',
            'metric': 'rmse',
            'subsample': subsample,
            'subsample_freq': int(subsample_freq),
            'learning_rate': learning_rate,
            'feature_fraction': feature_fraction,
            'max_depth': int(max_depth),
            'num_leaves': int(num_leaves),
            'min_data_in_leaf': int(min_data_in_leaf),
            'lambda_l1': lambda_l1,  
            'lambda_l2': lambda_l2,
            'early_stopping_rounds': int(early_stopping_rounds)
            }
    
    train_data = lgb.Dataset(X_train_with_cats, label=y_train)
    eval_data = lgb.Dataset(X_valid_with_cats, label=y_valid)
    gbm = lgb.train(params, train_data, valid_sets=eval_data)
    
    lgb_pred = gbm.predict(X_valid_with_cats)
    lgb_pred = get_class_pred(lgb_pred, reduce_train)
    
    return qwk3(y_valid, lgb_pred)

In [344]:
init_points = 25
n_iter = 50

bounds_lgb = {'n_estimators':(4000, 6000),
            'subsample': (0.6, 0.8),
            'subsample_freq': (0, 2),
            'learning_rate': (0.01, 0.02),
            'feature_fraction': (0.8, 1),
            'max_depth': (10, 20),
            'num_leaves': (2^10, 2^20),
            'min_data_in_leaf': (100, 2000),
            'lambda_l1': (1, 2),  
            'lambda_l2': (1, 2),
            'early_stopping_rounds': (90, 110)
            }

LGB_BO = BayesianOptimization(LGB_Bayesian, bounds_lgb, random_state=1029)

with warnings.catch_warnings():
    warnings.filterwarnings('ignore')
    LGB_BO.maximize(init_points=init_points, n_iter=n_iter, acq='ucb', xi=0.0, alpha=1e-6)

|   iter    |  target   | early_... | featur... | lambda_l1 | lambda_l2 | learni... | max_depth | min_da... | n_esti... | num_le... | subsample | subsam... |
-------------------------------------------------------------------------------------------------------------------------------------------------------------
[1]	valid_0's rmse: 1.25105
Training until validation scores don't improve for 90 rounds
[2]	valid_0's rmse: 1.24756
[3]	valid_0's rmse: 1.24414
[4]	valid_0's rmse: 1.24083
[5]	valid_0's rmse: 1.23928
[6]	valid_0's rmse: 1.23618
[7]	valid_0's rmse: 1.23351
[8]	valid_0's rmse: 1.23035
[9]	valid_0's rmse: 1.22742
[10]	valid_0's rmse: 1.22437
[11]	valid_0's rmse: 1.22155
[12]	valid_0's rmse: 1.2188
[13]	valid_0's rmse: 1.21609
[14]	valid_0's rmse: 1.21507
[15]	valid_0's rmse: 1.21409
[16]	valid_0's rmse: 1.21289
[17]	valid_0's rmse: 1.2103
[18]	valid_0's rmse: 1.20757
[19]	valid_0's rmse: 1.2051
[20]	valid_0's rmse: 1.20265
[21]	valid_0's rmse: 1.20038
[22]	valid_0's rmse: 1.198

[271]	valid_0's rmse: 1.04447
[272]	valid_0's rmse: 1.04432
[273]	valid_0's rmse: 1.04418
[274]	valid_0's rmse: 1.044
[275]	valid_0's rmse: 1.04385
[276]	valid_0's rmse: 1.04374
[277]	valid_0's rmse: 1.04356
[278]	valid_0's rmse: 1.0434
[279]	valid_0's rmse: 1.04327
[280]	valid_0's rmse: 1.04314
[281]	valid_0's rmse: 1.04296
[282]	valid_0's rmse: 1.04286
[283]	valid_0's rmse: 1.04272
[284]	valid_0's rmse: 1.04254
[285]	valid_0's rmse: 1.04245
[286]	valid_0's rmse: 1.04235
[287]	valid_0's rmse: 1.04221
[288]	valid_0's rmse: 1.04202
[289]	valid_0's rmse: 1.0419
[290]	valid_0's rmse: 1.04174
[291]	valid_0's rmse: 1.0416
[292]	valid_0's rmse: 1.04149
[293]	valid_0's rmse: 1.04137
[294]	valid_0's rmse: 1.04129
[295]	valid_0's rmse: 1.04109
[296]	valid_0's rmse: 1.04093
[297]	valid_0's rmse: 1.04078
[298]	valid_0's rmse: 1.04069
[299]	valid_0's rmse: 1.04053
[300]	valid_0's rmse: 1.04044
[301]	valid_0's rmse: 1.04033
[302]	valid_0's rmse: 1.04019
[303]	valid_0's rmse: 1.04006
[304]	valid_0's

[562]	valid_0's rmse: 1.01947
[563]	valid_0's rmse: 1.01942
[564]	valid_0's rmse: 1.01938
[565]	valid_0's rmse: 1.01936
[566]	valid_0's rmse: 1.01932
[567]	valid_0's rmse: 1.01928
[568]	valid_0's rmse: 1.01924
[569]	valid_0's rmse: 1.01919
[570]	valid_0's rmse: 1.01912
[571]	valid_0's rmse: 1.01905
[572]	valid_0's rmse: 1.01899
[573]	valid_0's rmse: 1.01895
[574]	valid_0's rmse: 1.0189
[575]	valid_0's rmse: 1.01887
[576]	valid_0's rmse: 1.01881
[577]	valid_0's rmse: 1.01876
[578]	valid_0's rmse: 1.01872
[579]	valid_0's rmse: 1.01868
[580]	valid_0's rmse: 1.01862
[581]	valid_0's rmse: 1.01856
[582]	valid_0's rmse: 1.01851
[583]	valid_0's rmse: 1.0185
[584]	valid_0's rmse: 1.01846
[585]	valid_0's rmse: 1.0184
[586]	valid_0's rmse: 1.01835
[587]	valid_0's rmse: 1.0183
[588]	valid_0's rmse: 1.01827
[589]	valid_0's rmse: 1.01825
[590]	valid_0's rmse: 1.01819
[591]	valid_0's rmse: 1.01815
[592]	valid_0's rmse: 1.01814
[593]	valid_0's rmse: 1.01807
[594]	valid_0's rmse: 1.01803
[595]	valid_0'

[844]	valid_0's rmse: 1.00965
[845]	valid_0's rmse: 1.00961
[846]	valid_0's rmse: 1.00958
[847]	valid_0's rmse: 1.00957
[848]	valid_0's rmse: 1.00954
[849]	valid_0's rmse: 1.00952
[850]	valid_0's rmse: 1.00949
[851]	valid_0's rmse: 1.00946
[852]	valid_0's rmse: 1.00944
[853]	valid_0's rmse: 1.00942
[854]	valid_0's rmse: 1.00939
[855]	valid_0's rmse: 1.00938
[856]	valid_0's rmse: 1.00935
[857]	valid_0's rmse: 1.00933
[858]	valid_0's rmse: 1.00932
[859]	valid_0's rmse: 1.0093
[860]	valid_0's rmse: 1.00928
[861]	valid_0's rmse: 1.00926
[862]	valid_0's rmse: 1.00923
[863]	valid_0's rmse: 1.0092
[864]	valid_0's rmse: 1.00917
[865]	valid_0's rmse: 1.00914
[866]	valid_0's rmse: 1.00914
[867]	valid_0's rmse: 1.00913
[868]	valid_0's rmse: 1.00909
[869]	valid_0's rmse: 1.00906
[870]	valid_0's rmse: 1.00904
[871]	valid_0's rmse: 1.00901
[872]	valid_0's rmse: 1.009
[873]	valid_0's rmse: 1.00897
[874]	valid_0's rmse: 1.00895
[875]	valid_0's rmse: 1.00892
[876]	valid_0's rmse: 1.0089
[877]	valid_0's

[1126]	valid_0's rmse: 1.00381
[1127]	valid_0's rmse: 1.00381
[1128]	valid_0's rmse: 1.0038
[1129]	valid_0's rmse: 1.00378
[1130]	valid_0's rmse: 1.00377
[1131]	valid_0's rmse: 1.00375
[1132]	valid_0's rmse: 1.00373
[1133]	valid_0's rmse: 1.00371
[1134]	valid_0's rmse: 1.00368
[1135]	valid_0's rmse: 1.00365
[1136]	valid_0's rmse: 1.00363
[1137]	valid_0's rmse: 1.00361
[1138]	valid_0's rmse: 1.00359
[1139]	valid_0's rmse: 1.00359
[1140]	valid_0's rmse: 1.00359
[1141]	valid_0's rmse: 1.00357
[1142]	valid_0's rmse: 1.00357
[1143]	valid_0's rmse: 1.00355
[1144]	valid_0's rmse: 1.00354
[1145]	valid_0's rmse: 1.00352
[1146]	valid_0's rmse: 1.0035
[1147]	valid_0's rmse: 1.00347
[1148]	valid_0's rmse: 1.00345
[1149]	valid_0's rmse: 1.00346
[1150]	valid_0's rmse: 1.00344
[1151]	valid_0's rmse: 1.00341
[1152]	valid_0's rmse: 1.0034
[1153]	valid_0's rmse: 1.00339
[1154]	valid_0's rmse: 1.00338
[1155]	valid_0's rmse: 1.00336
[1156]	valid_0's rmse: 1.00334
[1157]	valid_0's rmse: 1.00332
[1158]	vali

...

[848]	valid_0's rmse: 0.970496
[849]	valid_0's rmse: 0.970491
[850]	valid_0's rmse: 0.9705
[851]	valid_0's rmse: 0.970515
[852]	valid_0's rmse: 0.970515
[853]	valid_0's rmse: 0.970492
[854]	valid_0's rmse: 0.97046
[855]	valid_0's rmse: 0.970456
[856]	valid_0's rmse: 0.970447
[857]	valid_0's rmse: 0.970469
[858]	valid_0's rmse: 0.970459
[859]	valid_0's rmse: 0.970475
[860]	valid_0's rmse: 0.97046
[861]	valid_0's rmse: 0.970465
[862]	valid_0's rmse: 0.97048
[863]	valid_0's rmse: 0.970437
[864]	valid_0's rmse: 0.970396
[865]	valid_0's rmse: 0.970408
[866]	valid_0's rmse: 0.970401
[867]	valid_0's rmse: 0.970414
[868]	valid_0's rmse: 0.97043
[869]	valid_0's rmse: 0.970393
[870]	valid_0's rmse: 0.970409
[871]	valid_0's rmse: 0.970405
[872]	valid_0's rmse: 0.970408
[873]	valid_0's rmse: 0.970401
[874]	valid_0's rmse: 0.97041
[875]	valid_0's rmse: 0.970396
[876]	valid_0's rmse: 0.970407
[877]	valid_0's rmse: 0.970429
[878]	valid_0's rmse: 0.970406
[879]	valid_0's rmse: 0.970414
[880]	valid_0's

[34]	valid_0's rmse: 1.09914
[35]	valid_0's rmse: 1.0961
[36]	valid_0's rmse: 1.09442
[37]	valid_0's rmse: 1.09169
[38]	valid_0's rmse: 1.08931
[39]	valid_0's rmse: 1.08669
[40]	valid_0's rmse: 1.08404
[41]	valid_0's rmse: 1.08179
[42]	valid_0's rmse: 1.08021
[43]	valid_0's rmse: 1.07778
[44]	valid_0's rmse: 1.07553
[45]	valid_0's rmse: 1.07374
[46]	valid_0's rmse: 1.07225
[47]	valid_0's rmse: 1.07023
[48]	valid_0's rmse: 1.06809
[49]	valid_0's rmse: 1.06592
[50]	valid_0's rmse: 1.06414
[51]	valid_0's rmse: 1.06219
[52]	valid_0's rmse: 1.06035
[53]	valid_0's rmse: 1.05856
[54]	valid_0's rmse: 1.05689
[55]	valid_0's rmse: 1.05505
[56]	valid_0's rmse: 1.0533
[57]	valid_0's rmse: 1.05173
[58]	valid_0's rmse: 1.05036
[59]	valid_0's rmse: 1.04878
[60]	valid_0's rmse: 1.04739
[61]	valid_0's rmse: 1.04599
[62]	valid_0's rmse: 1.04456
[63]	valid_0's rmse: 1.04321
[64]	valid_0's rmse: 1.04189
[65]	valid_0's rmse: 1.0405
[66]	valid_0's rmse: 1.03914
[67]	valid_0's rmse: 1.03788
[68]	valid_0's rm

[314]	valid_0's rmse: 0.973646
[315]	valid_0's rmse: 0.973541
[316]	valid_0's rmse: 0.973555
[317]	valid_0's rmse: 0.973485
[318]	valid_0's rmse: 0.973512
[319]	valid_0's rmse: 0.97354
[320]	valid_0's rmse: 0.973517
[321]	valid_0's rmse: 0.973492
[322]	valid_0's rmse: 0.973518
[323]	valid_0's rmse: 0.973457
[324]	valid_0's rmse: 0.973403
[325]	valid_0's rmse: 0.97335
[326]	valid_0's rmse: 0.973323
[327]	valid_0's rmse: 0.973286
[328]	valid_0's rmse: 0.97328
[329]	valid_0's rmse: 0.973267
[330]	valid_0's rmse: 0.973264
[331]	valid_0's rmse: 0.973203
[332]	valid_0's rmse: 0.973199
[333]	valid_0's rmse: 0.973217
[334]	valid_0's rmse: 0.97318
[335]	valid_0's rmse: 0.973167
[336]	valid_0's rmse: 0.973094
[337]	valid_0's rmse: 0.973095
[338]	valid_0's rmse: 0.973117
[339]	valid_0's rmse: 0.9731
[340]	valid_0's rmse: 0.973138
[341]	valid_0's rmse: 0.973162
[342]	valid_0's rmse: 0.973124
[343]	valid_0's rmse: 0.973005
[344]	valid_0's rmse: 0.972956
[345]	valid_0's rmse: 0.97292
[346]	valid_0's

[176]	valid_0's rmse: 0.981606
[177]	valid_0's rmse: 0.981364
[178]	valid_0's rmse: 0.981239
[179]	valid_0's rmse: 0.981231
[180]	valid_0's rmse: 0.981101
[181]	valid_0's rmse: 0.980958
[182]	valid_0's rmse: 0.980794
[183]	valid_0's rmse: 0.980584
[184]	valid_0's rmse: 0.98046
[185]	valid_0's rmse: 0.980326
[186]	valid_0's rmse: 0.980259
[187]	valid_0's rmse: 0.980099
[188]	valid_0's rmse: 0.979961
[189]	valid_0's rmse: 0.979823
[190]	valid_0's rmse: 0.979758
[191]	valid_0's rmse: 0.979703
[192]	valid_0's rmse: 0.979572
[193]	valid_0's rmse: 0.979526
[194]	valid_0's rmse: 0.97937
[195]	valid_0's rmse: 0.979254
[196]	valid_0's rmse: 0.979029
[197]	valid_0's rmse: 0.978959
[198]	valid_0's rmse: 0.978755
[199]	valid_0's rmse: 0.978733
[200]	valid_0's rmse: 0.978632
[201]	valid_0's rmse: 0.97847
[202]	valid_0's rmse: 0.978437
[203]	valid_0's rmse: 0.978358
[204]	valid_0's rmse: 0.978329
[205]	valid_0's rmse: 0.978177
[206]	valid_0's rmse: 0.97811
[207]	valid_0's rmse: 0.978058
[208]	valid_

[452]	valid_0's rmse: 0.971029
[453]	valid_0's rmse: 0.971012
[454]	valid_0's rmse: 0.971011
[455]	valid_0's rmse: 0.970984
[456]	valid_0's rmse: 0.970924
[457]	valid_0's rmse: 0.970918
[458]	valid_0's rmse: 0.970861
[459]	valid_0's rmse: 0.970811
[460]	valid_0's rmse: 0.970796
[461]	valid_0's rmse: 0.970769
[462]	valid_0's rmse: 0.970733
[463]	valid_0's rmse: 0.970706
[464]	valid_0's rmse: 0.970684
[465]	valid_0's rmse: 0.970627
[466]	valid_0's rmse: 0.970615
[467]	valid_0's rmse: 0.970579
[468]	valid_0's rmse: 0.970571
[469]	valid_0's rmse: 0.970462
[470]	valid_0's rmse: 0.97047
[471]	valid_0's rmse: 0.970474
[472]	valid_0's rmse: 0.970399
[473]	valid_0's rmse: 0.970345
[474]	valid_0's rmse: 0.970416
[475]	valid_0's rmse: 0.970452
[476]	valid_0's rmse: 0.970453
[477]	valid_0's rmse: 0.970398
[478]	valid_0's rmse: 0.970353
[479]	valid_0's rmse: 0.970365
[480]	valid_0's rmse: 0.970351
[481]	valid_0's rmse: 0.970311
[482]	valid_0's rmse: 0.970402
[483]	valid_0's rmse: 0.97049
[484]	vali

In [345]:
print(LGB_BO.max)

{'target': 0.6108369866199699, 'params': {'early_stopping_rounds': 107.18952981762907, 'feature_fraction': 0.8038429377037525, 'lambda_l1': 1.2014023060102834, 'lambda_l2': 1.3903775193367474, 'learning_rate': 0.015408194226473406, 'max_depth': 10.013835565382186, 'min_data_in_leaf': 119.12989958061449, 'n_estimators': 5414.877032329807, 'num_leaves': 20.942615517293138, 'subsample': 0.6323822894317168, 'subsample_freq': 0.055598144844630326}}


In [348]:
params = {'n_estimators': int(LGB_BO.max['params']['n_estimators']),
            'boosting_type': 'gbdt',
            'objective': 'regression',
            'metric': 'rmse',
            'subsample': LGB_BO.max['params']['subsample'],
            'subsample_freq': int(LGB_BO.max['params']['subsample_freq']),
            'learning_rate': LGB_BO.max['params']['learning_rate'],
            'feature_fraction': LGB_BO.max['params']['feature_fraction'],
            'max_depth': int(LGB_BO.max['params']['max_depth']),
            'num_leaves': int(LGB_BO.max['params']['num_leaves']),
            'min_data_in_leaf': int(int(LGB_BO.max['params']['min_data_in_leaf'])),
            'lambda_l1': LGB_BO.max['params']['lambda_l1'],  
            'lambda_l2':LGB_BO.max['params']['lambda_l2'],
            'early_stopping_rounds': int(LGB_BO.max['params']['early_stopping_rounds'])
            }

train_data = lgb.Dataset(X_train_with_cats, label=y_train)
eval_data = lgb.Dataset(X_valid_with_cats, label=y_valid)
gbm = lgb.train(params, train_data, valid_sets=eval_data)

[1]	valid_0's rmse: 1.24836
Training until validation scores don't improve for 107 rounds
[2]	valid_0's rmse: 1.24573
[3]	valid_0's rmse: 1.24209
[4]	valid_0's rmse: 1.236
[5]	valid_0's rmse: 1.23012
[6]	valid_0's rmse: 1.22438
[7]	valid_0's rmse: 1.21884
[8]	valid_0's rmse: 1.2135
[9]	valid_0's rmse: 1.20821
[10]	valid_0's rmse: 1.20302
[11]	valid_0's rmse: 1.19795
[12]	valid_0's rmse: 1.19313
[13]	valid_0's rmse: 1.1883
[14]	valid_0's rmse: 1.18371
[15]	valid_0's rmse: 1.17922
[16]	valid_0's rmse: 1.17502
[17]	valid_0's rmse: 1.1706
[18]	valid_0's rmse: 1.16723
[19]	valid_0's rmse: 1.16309
[20]	valid_0's rmse: 1.15902
[21]	valid_0's rmse: 1.15531
[22]	valid_0's rmse: 1.15148
[23]	valid_0's rmse: 1.1479
[24]	valid_0's rmse: 1.14592
[25]	valid_0's rmse: 1.14392
[26]	valid_0's rmse: 1.14176
[27]	valid_0's rmse: 1.13823
[28]	valid_0's rmse: 1.13479
[29]	valid_0's rmse: 1.13151
[30]	valid_0's rmse: 1.12822
[31]	valid_0's rmse: 1.12517
[32]	valid_0's rmse: 1.12207
[33]	valid_0's rmse: 1.11

[287]	valid_0's rmse: 0.976774
[288]	valid_0's rmse: 0.976779
[289]	valid_0's rmse: 0.976652
[290]	valid_0's rmse: 0.97659
[291]	valid_0's rmse: 0.976534
[292]	valid_0's rmse: 0.976464
[293]	valid_0's rmse: 0.976331
[294]	valid_0's rmse: 0.976351
[295]	valid_0's rmse: 0.976305
[296]	valid_0's rmse: 0.976201
[297]	valid_0's rmse: 0.976114
[298]	valid_0's rmse: 0.976029
[299]	valid_0's rmse: 0.976013
[300]	valid_0's rmse: 0.975959
[301]	valid_0's rmse: 0.975888
[302]	valid_0's rmse: 0.975858
[303]	valid_0's rmse: 0.975875
[304]	valid_0's rmse: 0.975808
[305]	valid_0's rmse: 0.975708
[306]	valid_0's rmse: 0.975653
[307]	valid_0's rmse: 0.97564
[308]	valid_0's rmse: 0.975609
[309]	valid_0's rmse: 0.97556
[310]	valid_0's rmse: 0.975441
[311]	valid_0's rmse: 0.975425
[312]	valid_0's rmse: 0.975307
[313]	valid_0's rmse: 0.975247
[314]	valid_0's rmse: 0.975194
[315]	valid_0's rmse: 0.975198
[316]	valid_0's rmse: 0.975194
[317]	valid_0's rmse: 0.975107
[318]	valid_0's rmse: 0.975031
[319]	valid

[567]	valid_0's rmse: 0.970879
[568]	valid_0's rmse: 0.970865
[569]	valid_0's rmse: 0.970815
[570]	valid_0's rmse: 0.970757
[571]	valid_0's rmse: 0.97073
[572]	valid_0's rmse: 0.970723
[573]	valid_0's rmse: 0.970708
[574]	valid_0's rmse: 0.970679
[575]	valid_0's rmse: 0.97067
[576]	valid_0's rmse: 0.970684
[577]	valid_0's rmse: 0.970696
[578]	valid_0's rmse: 0.970659
[579]	valid_0's rmse: 0.970687
[580]	valid_0's rmse: 0.970618
[581]	valid_0's rmse: 0.970614
[582]	valid_0's rmse: 0.970632
[583]	valid_0's rmse: 0.970602
[584]	valid_0's rmse: 0.970595
[585]	valid_0's rmse: 0.970626
[586]	valid_0's rmse: 0.97067
[587]	valid_0's rmse: 0.970676
[588]	valid_0's rmse: 0.970623
[589]	valid_0's rmse: 0.970629
[590]	valid_0's rmse: 0.970636
[591]	valid_0's rmse: 0.970647
[592]	valid_0's rmse: 0.970631
[593]	valid_0's rmse: 0.970654
[594]	valid_0's rmse: 0.970604
[595]	valid_0's rmse: 0.970611
[596]	valid_0's rmse: 0.970632
[597]	valid_0's rmse: 0.97059
[598]	valid_0's rmse: 0.970568
[599]	valid_

[840]	valid_0's rmse: 0.970241
[841]	valid_0's rmse: 0.970308
[842]	valid_0's rmse: 0.970274
[843]	valid_0's rmse: 0.970324
[844]	valid_0's rmse: 0.970363
[845]	valid_0's rmse: 0.97036
[846]	valid_0's rmse: 0.970374
[847]	valid_0's rmse: 0.970342
[848]	valid_0's rmse: 0.970323
[849]	valid_0's rmse: 0.970351
[850]	valid_0's rmse: 0.970377
[851]	valid_0's rmse: 0.970354
[852]	valid_0's rmse: 0.970343
[853]	valid_0's rmse: 0.970383
[854]	valid_0's rmse: 0.970381
[855]	valid_0's rmse: 0.970386
[856]	valid_0's rmse: 0.97035
[857]	valid_0's rmse: 0.970353
[858]	valid_0's rmse: 0.970371
[859]	valid_0's rmse: 0.970347
[860]	valid_0's rmse: 0.97036
[861]	valid_0's rmse: 0.970392
[862]	valid_0's rmse: 0.9704
[863]	valid_0's rmse: 0.970427
[864]	valid_0's rmse: 0.970414
[865]	valid_0's rmse: 0.970344
[866]	valid_0's rmse: 0.970352
[867]	valid_0's rmse: 0.97034
[868]	valid_0's rmse: 0.970372
[869]	valid_0's rmse: 0.970403
[870]	valid_0's rmse: 0.970376
[871]	valid_0's rmse: 0.970375
[872]	valid_0'

In [339]:
lgb_pred = gbm.predict(X_valid_with_cats)
lgb_pred = get_class_pred(lgb_pred, reduce_train)
lgb_train_pred = get_class_pred(gbm.predict(X_train_with_cats), reduce_train)
    
print('Train accuracy score:',qwk3(y_train,lgb_train_pred))
print('Test accuracy score:',qwk3(y_valid,lgb_pred))
# 0.6111954969961837

Train accuracy score: 0.7382395119854381
Test accuracy score: 0.6111954969961837


In [349]:
del LGB_BO, bounds_lgb
gc.collect()

870

In [350]:
def find_weights(rf, knn, xgb, cat, cnn, lgb):
    weights = {'rf': rf, 'knn': knn, 'xgb': xgb, 'cat': cat, 'cnn': cnn, 'lgb': lgb}

    final_pred = (rf_pred_y * weights['rf']) + \
        (knn_pred_y * weights['knn']) + \
        (bst_pred * weights['xgb']) + \
        (cat_pred * weights['cat']) + \
        (nn_pred_y * weights['cnn']) + \
        (lgb_pred * weights['lgb'])
    
    final_pred = get_class_pred(final_pred, reduce_train)

    return qwk3(y_valid,final_pred)

In [302]:
init_points = 25
n_iter = 50

bounds_weights = {'rf': (0, 1), 
           'knn': (0, 1),  
           'xgb': (0, 1), 
           'cat': (0, 1),  
           'cnn': (0, 1),
           'lgb': (0, 1)
          }

Weights_BO = BayesianOptimization(find_weights, bounds_weights, random_state=1029)

with warnings.catch_warnings():
    warnings.filterwarnings('ignore')
    Weights_BO.maximize(init_points=init_points, n_iter=n_iter, acq='ucb', xi=0.0, alpha=1e-6)

|   iter    |  target   |    cat    |    cnn    |    knn    |    lgb    |    rf     |    xgb    |
-------------------------------------------------------------------------------------------------
|  1        |  0.6053   |  0.04104  |  0.4098   |  0.5887   |  0.8999   |  0.1211   |  0.1702   |
|  2        |  0.6047   |  0.9402   |  0.5953   |  0.3357   |  0.4417   |  0.4958   |  0.0879   |
|  3        |  0.5961   |  0.2742   |  0.66     |  0.08033  |  0.03865  |  0.6751   |  0.1873   |
|  4        |  0.6044   |  0.9393   |  0.8712   |  0.3583   |  0.5678   |  0.8793   |  0.4525   |
|  5        |  0.6007   |  0.7051   |  0.7962   |  0.9438   |  0.3038   |  0.9095   |  0.5      |
|  6        |  0.6045   |  0.03881  |  0.2672   |  0.1164   |  0.284    |  0.4905   |  0.7572   |
|  7        |  0.5988   |  0.7069   |  0.5281   |  0.8701   |  0.02299  |  0.3082   |  0.1684   |
|  8        |  0.6029   |  0.426    |  0.7768   |  0.5344   |  0.2915   |  0.4713   |  0.6732   |
|  9        |  0.604

|  51       |  0.6116   |  0.541    |  0.02475  |  0.004427 |  0.6655   |  0.06672  |  0.8306   |
|  52       |  0.6136   |  0.984    |  0.01383  |  0.08266  |  0.4398   |  0.008672 |  0.9645   |
|  53       |  0.6106   |  0.9683   |  0.02745  |  0.0142   |  0.2947   |  0.3107   |  0.9852   |
|  54       |  0.6116   |  0.8243   |  0.00703  |  0.02294  |  0.6107   |  0.000641 |  0.9137   |
|  55       |  0.6107   |  0.9925   |  0.01465  |  0.09405  |  0.5106   |  0.1162   |  0.9643   |
|  56       |  0.6112   |  0.9297   |  0.000941 |  0.03094  |  0.3022   |  0.008561 |  0.9152   |
|  57       |  0.6117   |  0.9383   |  0.06051  |  0.007856 |  0.6332   |  0.01307  |  0.9307   |
|  58       |  0.6119   |  0.5182   |  0.007823 |  0.013    |  0.5988   |  0.1214   |  0.9963   |
|  59       |  0.6117   |  0.744    |  0.002095 |  0.03419  |  0.5914   |  0.01239  |  0.9157   |
|  60       |  0.6119   |  0.783    |  0.02861  |  0.007455 |  0.5566   |  0.000362 |  0.834    |
|  61       |  0.611

In [ ]:
final_pred = (rf_pred_y * Weights_BO.max['params']['rf']) + \
    (knn_pred_y * Weights_BO.max['params']['knn']) + \
    (bst_pred * Weights_BO.max['params']['xgb']) + \
    (cat_pred * Weights_BO.max['params']['cat']) + \
    (nn_pred_y * Weights_BO.max['params']['cnn'] + \
    (lgb_pred * Weights_BO.max['params']['lgb']))

final_pred = get_class_pred(final_pred, reduce_train)


print('Test accuracy score:',qwk3(y_valid,final_pred))

# 0.6123981493146219 Local

In [315]:
# Make final predictions
X_test_with_cats, _ = create_cats(test, X_valid, categoricals)
X_test_with_cats, _ = create_min_max(X_test_with_cats, X_valid, categoricals)
X_test_with_cats.columns = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in X_test_with_cats.columns]

rf_test_pred = rf.predict(X_test_with_cats)
knn_test_pred = knn.predict(X_test_with_cats)
bst_test_pred = get_class_pred(bst.predict(xgb.DMatrix(X_test_with_cats)), reduce_train)
cat_test_pred = get_class_pred(cat.predict(X_test_with_cats), reduce_train)
nn_test_pred = model.predict(X_test_with_cats)
lgb_test_pred = gbm.predict(X_test_with_cats)

final_pred = (rf_test_pred * Weights_BO.max['params']['rf']) + \
    (knn_test_pred * Weights_BO.max['params']['knn']) + \
    (bst_test_pred * Weights_BO.max['params']['xgb']) + \
    (cat_test_pred * Weights_BO.max['params']['cat']) + \
    (nn_test_pred * Weights_BO.max['params']['cnn'] + \
    (lgb_test_pred * Weights_BO.max['params']['lgb']))

final_pred = get_class_pred(final_pred, reduce_train)

Test accuracy score: 0.6123981493146219


In [351]:
submission = pd.DataFrame()
submission['installation_id'] = adjusted_test['installation_id']
submission['accuracy_group'] = final_pred.astype(int)
submission.to_csv('submission.csv', index=False)
submission['accuracy_group'].value_counts(normalize=True)

NameError: name 'adjusted_test' is not defined